# Introduction

This notebook presents a methodology for assessing how well the Bureau's official forecast product captures diurnal (i.e daily) wind processes compared to model products like the Operational Consensus Forecast (OCF), the Australian Community Climate and Earth-System Simulator (ACCESS) forecast, and the European Center for Medium-Range Weather Forecasting (ECMWF) forecast. The official forecast is typically constructed from a blend of model outputs that are then edited by human forecasters, whereas the OCF, ACCESS and ECMWF forecasts represent unedited model output. Comparing these products therefore provides insight into the "added value" provided by human forecasters. The analysis presented here is based purely on accuracy in a physical science sense; the analysis cannot account for the social, political or economic reasons human forecasters may have for over or under forecasting certain events or processes.

## Daily Performance 

<a id='daily_perturbation_index_definitions'></a> The methodology for comparing the official forecast to one of the model forecasts (OCF, ACCESS or ECMWF) is based on comparing each to station observations, and can be summarised as follows.
1. Isolate the diurnal signal in the observational data, the official forecast and model forecast by subtracting a twenty four hour centred running mean at each time step. The resulting datasets describe the _wind perturbations_ from the 24 hour average _background wind_.
2. At each time step calculate the quantity $\text{WPI}_{\text{off}} \equiv \left\lvert \boldsymbol{u}_{\text{obs}}-\boldsymbol{u}_{\text{off}} \right\rvert$ which is the magnitude of the vector difference between the observed and official forecast wind perturbations. Calculate $\text{WPI}_{\text{mod}}$ analogously, and define the _Wind Perturbation Index_ $\text{WPI} \equiv \text{WPI}_{\text{mod}} - \text{WPI}_{\text{off}}$. The official forecast wind perturbation at a given time will be closer to the observed perturbation than that of the model if and only if $\text{WPI} > 0$.
3. Aggregate $\text{WPI}$ on an hourly basis, and calculate the mean and the sampling distribution of the mean for each hour. 

Note the first step is necessary because if raw wind fields are compared, differences in winds between datasets will be dominated by the typically larger differences in the daily mean winds of each dataset. Put another way, the _changes_ in the wind throughout a given day in a given forecast may match the way the winds change in observations, _even if_ the observed and forecast winds are different. Therefore, not subtracting a daily average background wind may result in the conclusion that diurnal processes (like land-sea breezes) are being treated poorly, when actually the errors come from processes occurring on longer timescales, such as poorly forecast synoptic pressure systems or monsoon processes. In the case of land-sea breezes, thinking in terms of perturbations may require a slight conceptual shift from the usual operational definitions; even if the wind is offshore the entire day, "sea-breeze perturbations" may still be detected as a weakening in the offshore winds throughout the afternoon and evening. 

## Climatological Performance

<a id='climatological_perturbation_index_definitions'></a> Although the above methodology is perhaps the most relevant for assessing forecast performance in an operational sense, it is also informative to think about how well each forecast product performs in a climatological sense, i.e to ask how well the _mean_ forecast perturbation winds match the _mean_ observed perturbations over a suitable climatological period. To accomplish this, steps 2 and three above are modified as follows.
- Average the perturbations at each hour across the climatological period, i.e average all the 00:00 UTC perturbations, all the 01:00 UTC perturbations, and so forth. Calculate the quantity $\text{CWPI}_{\text{off}} \equiv \left\lvert \bar{\boldsymbol{u}}_{\text{obs}}-\bar{\boldsymbol{u}}_{\text{off}} \right\rvert$. This represents the magnitude of the vector difference between the observed _mean_ wind perturbations and official forecast _mean_ wind perturbations. Calculate $\text{CWPI}_{\text{mod}}$ analogously and define the the _Climatological Wind Perturbation Index_ $\text{CWPI} = \text{CWPI}_{\text{mod}} - \text{CWPI}_{\text{off}}$.
- Calculate the sampling distribution of $\text{CWPI}$ by bootstrapping (e.g [https://www.doi.org/10.1214/aos/1176344552](https://www.doi.org/10.1214/aos/1176344552).)  


# Setup 

Begin by importing the necessary python modules.

In [1]:
# Debug
import pdb

# Core
import datetime
import warnings

# File management
import sys
import pickle

# Analysis
import pandas as pd
import numpy as np
import xarray as xr
from scipy.stats import t
from scipy.optimize import least_squares
import scipy.stats as ss

# Plotting
import plotly
import plotly.graph_objs as go
from plotly.offline import iplot
plotly.offline.init_notebook_mode()
from plotly import tools
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
import seaborn as sns

# Rendering as HTML
import IPython.core.display as di

# Jive
from jive.dataviews import gfe_pt, obs_pt
from jive.spatial.stations import StationData
from jive.metrics.standard.deterministic import mse
from jive.metrics.processing import magnitude_of_vector_diff
from jive.metrics.processing import polar2cartesian_met
from jive.metrics.processing import cartesian2polar_met
from jive.utils.xrtools import broadcast_and_match_nan
from jive.spatial.stations import StationGrouping
from jive.metrics import stats
#from eta_verification.projects import CacheWarehouse

2019-03-14 15:37:59,774:jive:INFO: Config file /Users/Ewan/anaconda3/envs/jive/lib/python3.6/site-packages/Jive-1.3.1-py3.6.egg/jive/default_config.yml loaded.
2019-03-14 15:37:59,819:jive:INFO: Config file /Users/Ewan/jive_home/config.yml loaded.


Set HTML rendered output to suppress code cells by default. 

In [2]:
di.display_html(
    '<script>jQuery(function() {if (jQuery("body.notebook_app").length ==' + \
    '0) { jQuery(".input_area, .output_stderr").toggle(); jQuery(".prompt"' + \
    ').toggle();}});</script>', raw=True)

## Functions 

Define the functions used in this section.  

In [3]:
def load_obs_data(
    dir_filename, mag_filename ,stations, start_date, end_date
):
    """
    Load station data from file if it exists or the Jive database if it doesn't.
    """
    try:
        obs_dir = xr.open_dataarray(dir_filename)
        obs_mag = xr.open_dataarray(mag_filename)
        
        for attr in ['valid_start', 'valid_end']:
            obs_dir.attrs[attr] = np.datetime64(obs_dir.attrs[attr])
            obs_mag.attrs[attr] = np.datetime64(obs_mag.attrs[attr])
    except:
        obs_dir = obs_pt.WindDir(
            valid_start_date=start_date,
            valid_end_date=end_date,
            stations=list(stations))

        obs_mag = obs_pt.WindMag(
            valid_start_date=start_date,
            valid_end_date=end_date,
            stations=list(stations))
        
        # Make copies so attributes can be converted to strings and saved as .nc 
        obs_dir_nc = obs_dir
        obs_mag_nc = obs_mag
        
        for attr in ['valid_start', 'valid_end']:
            obs_dir_nc.attrs[attr] = str(obs_dir_nc.attrs[attr])
            obs_mag_nc.attrs[attr] = str(obs_mag_nc.attrs[attr])
            
        obs_dir_nc.to_netcdf(dir_filename, mode='w')
        obs_mag_nc.to_netcdf(mag_filename, mode='w')
        
    return obs_dir, obs_mag

def load_mod_data(
    dir_filename, mag_filename, source, b_hour, stations, dates
):
    """
    Load model data from file if it exists or Jive database if it doesn't.
    """
    try:
        mod_dir = xr.open_dataarray(dir_filename)
        mod_mag = xr.open_dataarray(mag_filename)
        
        mod_dir['valid_start']=mod_dir['valid_start'].astype(np.datetime64)
        mod_mag['valid_start']=mod_mag['valid_start'].astype(np.datetime64)
    except:
        
        mod_dir_parts = []
        mod_mag_parts = []
        
        for start_date, end_date in dates:
            mod_dir_part = gfe_pt.WindDir(
                valid_start_date=start_date,
                valid_end_date=end_date,
                source_id=source,
                base_hour=b_hour,
                stations=stations
            )
            
            mod_mag_part = gfe_pt.WindMag(
                valid_start_date=start_date,
                valid_end_date=end_date,
                source_id=source,
                base_hour=b_hour,
                stations=stations
            )
            print('Got data for {} - {}'.format(start_date, end_date))
            mod_dir_parts.append(mod_dir_part)
            mod_mag_parts.append(mod_mag_part)
            
        mod_dir = xr.concat(mod_dir_parts, dim='valid_start')
        mod_mag = xr.concat(mod_mag_parts, dim='valid_start')
        
        # Make copies so attributes can be converted to strings and saved as .nc 
        mod_dir_nc = mod_dir
        mod_mag_nc = mod_mag
        
        mod_dir_nc['valid_start']=mod_dir_nc['valid_start'].astype(str)
        mod_mag_nc['valid_start']=mod_mag_nc['valid_start'].astype(str)
            
        mod_dir_nc.to_netcdf(dir_filename, mode='w')
        mod_mag_nc.to_netcdf(mag_filename, mode='w')
        
    return mod_dir, mod_mag

## Generate Datasets ##

First, specify the dates and stations of interest: this notebook will consider the winter months (June, July, August) of 2017 and the stations within 200 km of a coastline. To resolve land-sea breezes it can be helpful to combine data for stations along stretches of coastline with the same orientation. For the northern territory stations three groups are defined. 
1. Stations along the west coast: Mango Farm, Port Keats Airport, Channel Point, Dum in Mirrie Airstrip, Darwin NTC AWS, Fish Reef Marine, Charles Point, Point Stuart, Middle Point, Noonamah Airstrip, and Kangaroo Flats.
2. Stations along the north coast: Murganella Airstrip, Warruwi Airport, Wilingimbi Airport, and Ngayawili.
3. Tiwi Islands stations: Point Fawcett and Pirlangimpi Airport.

In [4]:
# For conveniently loading 'wet' and 'dry' season files from Jupyterhub.
season = 'austral_winter'

# Specify dates.
if season == 'austral_winter':
    start_date="20180531"
    end_date="20180901"
    # Break interval into ten day segments to deal with server memory issues
    dates = [
        ('20180531', '20180610'),
        ('20180611', '20180620'),
        ('20180621', '20180630'),
        ('20180701', '20180710'),
        ('20180711', '20180720'),
        ('20180721', '20180731'),
        ('20180801', '20180810'),
        ('20180811', '20180820'),
        ('20180821', '20180901')
    ]
    
elif season == 'austral_summer':
    start_date="20171130"
    end_date="20180301"
    # Break interval into ten day segments to deal with server memory issues
    dates = [
        ('20171130', '20171210'),
        ('20171211', '20171220'),
        ('20171221', '20171231'),
        ('20180101', '20180110'),
        ('20180111', '20180120'),
        ('20180121', '20180131'),
        ('20180201', '20180210'),
        ('20180211', '20180220'),
        ('20180221', '20180301'),
    ]

# Station information class.
all_station_data = StationData()

# Coastal stations.
coastal_stations=all_station_data.get(
    distance_from_coast=[None, 150]
)

# Copied from define_station_groups.py
exclude_from_wind = {
    66208,  # Wattamolla, NSW
    61392,  # Murrurundi Gap, NSW
    59040,  # Coffs Harbour Met Office, NSW
    86266,  # Ferny Creek, VIC
    85096,  # Wilsons Promentary, VIC
    200838,  # Hogan Island, VIC
    82139,  # Hunters Hill, VIC
    84143,  # Combienbar AWS, VIC
    85291,  # Mt Baw Baw, VIC
    85296,  # Mt Moornapa, VIC
    84144,  # Mt Nowa Nowa, VIC
    79101,  # Ben Nevis, VIC
    400139,  # Kingfish B, VIC
    91344,  # Burnie NTC AWS, TAS
    94941,  # Maatsuker Is, TAS
    14072,  # Darwin NTC AWS, NT
    40043,  # Cape Moreton, QLD
    27054,  # Coconut Island, QLD
    40068,  # Double Island Point, QLD
    40284,  # Beerburrum, QLD
    29182,  # Mornington Island AP
    33106,  # Hamilton Is, QLD
    39322,  # Rundle Island, QLD
    40913  # Brisbane, QLD
}

coastal_stations = coastal_stations - exclude_from_wind

darwin_ap_stations = [
    14015, 14031, 14277, 14254, 14314, 14142, 200731, 14272, 14041, 14983
]

brisbane_ap_stations = [
    40842, 40764, 40958, 40926, 40043, 40927, 40211, 40988, 40861, 40908
]

sydney_ap_stations = [
    66037, 66051, 66043, 66194, 66022, 66196, 66197, 66059, 66137, 68257
]

canberra_ap_stations = [
    70330, 70351, 70339, 70349, 70217, 71075, 71032, 68072, 69132, 68239,
]

melbourne_ap_stations = [
    86282, 86038, 86383, 86068, 86338, 86220, 87031, 86376, 86077, 87113
]

hobart_ap_stations = [
    94008, 94212, 92124, 94254, 94029, 94087, 94220, 94255, 94155, 94198
]

adelaide_ap_stations = [
    23034, 23052, 23083, 23122, 23013, 23000, 23885, 23886, 23842, 23887
]

perth_ap_stations = [
    9225, 9215, 9021, 9091, 9240, 9172, 9193, 9256, 9281, 9053
]

all_station_groups = np.stack(
    [hobart_ap_stations, melbourne_ap_stations, canberra_ap_stations, 
    adelaide_ap_stations, sydney_ap_stations, perth_ap_stations, 
    brisbane_ap_stations, darwin_ap_stations], axis=0
)

airport_station_group_names = [
    'hobart_ap_stations', 'melbourne_ap_stations', 'canberra_ap_stations', 
    'adelaide_ap_stations', 'sydney_ap_stations', 'perth_ap_stations', 
    'brisbane_ap_stations', 'darwin_ap_stations'
]
# Create a dictionary for capital city stations.
airport_stations = {
    'canberra AP' : 70351, 
    'sydney AP' : 66037, 
    'darwin AP' : 14015, 
    'melbourne AP' : 86282,
    'adelaide AP' : 23034,
    'perth AP' : 9021,
    'brisbane AP' : 40842,
    'hobart AP' : 94008,
    'cairns AP' : 31011,
    'townsville AP' : 32040,
    'geraldton AP' : 8315,
    'mount gambier AP' : 26021,
    'mount hotham AP' : 83055,
}

airport_station_list = [
    14015, 40842, 9021, 66037, 23034, 70351, 86282, 94008, 
]
airport_station_list.reverse()

darwin_ap = [14015]
brisbane_ap = [40842]
perth_ap = [9021]
sydney_ap = [66037]
adelaide_ap = [23034]
canberra_ap = [70351]
melbourne_ap = [86282]
hobart_ap = [94008]

airport_names = [
    'darwin_ap', 'brisbane_ap', 'perth_ap', 'sydney_ap', 'adelaide_ap', 
    'canberra_ap', 'melbourne_ap', 'hobart_ap'
]
airport_names.reverse()

airport_station_list = [
    14015, 40842, 9021, 66037, 23034, 70351, 86282, 94008, 
]
airport_station_list.reverse()

airport_station_list_lab = [
    'Darwin', 'Brisbane', 'Perth', 
    'Sydney', 'Adelaide', 'Canberra', 'Melbourne', 'Hobart',
]
airport_station_list_lab.reverse()

distance = 100

wa_coastal_north = all_station_data.get(regions=['WA'], distance_from_coast=[0, distance], latitude=[-21.819, 0])
wa_coastal_west = all_station_data.get(regions=['WA'], distance_from_coast=[0, distance], latitude=[-35.01, -21.819], longitude=[110,116])
wa_coastal_south = all_station_data.get(regions=['WA'], distance_from_coast=[0, distance], 
                                        latitude=[-40, -31], longitude=[116.6, 140]) - {10917}
sa_coastal = all_station_data.get(regions=['SA'], distance_from_coast=[0, distance],
                                 latitude=[-40, -30.5])
vic_coastal = all_station_data.get(regions=['VIC'], distance_from_coast=[0, distance])
nsw_coastal = all_station_data.get(regions=['NSW'], distance_from_coast=[0, distance])
qld_coastal = all_station_data.get(regions=['QLD'], distance_from_coast=[0, distance], 
                                   longitude=[142.17, 160], latitude=[-30, -18.47])
nt_coastal = all_station_data.get(regions=['NT'], distance_from_coast=[0, distance], latitude=[-14, -9])

coastal_station_group_names = [
    'nt_coastal', 'qld_coastal', 'wa_coastal_north', 'wa_coastal_west', 'wa_coastal_south',
    'nsw_coastal', 'sa_coastal', 'vic_coastal', 
]
coastal_station_group_names.reverse()

coastal_station_group_labels = ['NT', 'QLD', 'North WA',  'West WA', 'South WA', 'NSW', 'SA', 'VIC']
coastal_station_group_labels.reverse()

Save station data for use in external map making script.

In [5]:
nt_coastal_df = all_station_data.all_data(nt_coastal)
qld_coastal_df = all_station_data.all_data(qld_coastal)
nsw_coastal_df = all_station_data.all_data(nsw_coastal)
vic_coastal_df = all_station_data.all_data(vic_coastal)
sa_coastal_df = all_station_data.all_data(sa_coastal)
wa_coastal_south_df = all_station_data.all_data(wa_coastal_south)
wa_coastal_west_df = all_station_data.all_data(wa_coastal_west)
wa_coastal_north_df = all_station_data.all_data(wa_coastal_north)

darwin_ap_stations_df = all_station_data.all_data(darwin_ap_stations)
brisbane_ap_stations_df = all_station_data.all_data(brisbane_ap_stations)
sydney_ap_stations_df = all_station_data.all_data(sydney_ap_stations)
canberra_ap_stations_df = all_station_data.all_data(canberra_ap_stations)
melbourne_ap_stations_df = all_station_data.all_data(melbourne_ap_stations)
hobart_ap_stations_df = all_station_data.all_data(hobart_ap_stations)
adelaide_ap_stations_df = all_station_data.all_data(adelaide_ap_stations)
perth_ap_stations_df = all_station_data.all_data(perth_ap_stations)

station_df = (
    nt_coastal_df, qld_coastal_df, nsw_coastal_df, vic_coastal_df, sa_coastal_df, wa_coastal_south_df, 
    wa_coastal_west_df, wa_coastal_north_df, darwin_ap_stations_df, brisbane_ap_stations_df, 
    sydney_ap_stations_df, canberra_ap_stations_df, melbourne_ap_stations_df, hobart_ap_stations_df,
    adelaide_ap_stations_df, perth_ap_stations_df
)

with open("station_df.pkl","wb") as output:
    pickle.dump(station_df,output)

Next, load the wind direction and magnitude fields for each dataset. 

In [6]:
# AWS Observations
obs_dir,obs_mag = load_obs_data(
    './Coastal_Data/aws_hourly_airport_' + start_date + '_' + end_date + '_dir.nc', 
    './Coastal_Data/aws_hourly_airport_' + start_date + '_' + end_date + '_mag.nc',
    coastal_stations, start_date, end_date
)

In [7]:
# Official
off_dir,off_mag = load_mod_data(
    './Coastal_Data/Op_Official_airport_' + start_date + '_' + end_date + '_dir.nc', 
    './Coastal_Data/Op_Official_airport_' + start_date + '_' + end_date + '_mag.nc', 
    'Op_Official', 00, coastal_stations, dates
)

In [8]:
# OCF
ocf_dir, ocf_mag = load_mod_data(
    './Coastal_Data/Op_OCF_airport_' + start_date + '_' + end_date + '_dir.nc', 
    './Coastal_Data/Op_OCF_airport_' + start_date + '_' + end_date + '_mag.nc', 
    'Op_OCF', 18, coastal_stations, dates
)

In [9]:
# ACCESS
acc_dir, acc_mag = load_mod_data(
    './Coastal_Data/Op_AAust_airport_' + start_date + '_' + end_date + '_dir.nc', 
    './Coastal_Data/Op_AAust_airport_' + start_date + '_' + end_date + '_mag.nc',
    'Op_AAust', 18, coastal_stations, dates
)

In [10]:
# ECMWF
ecm_dir, ecm_mag = load_mod_data(
    './Coastal_Data/Op_ECMWF_airport_' + start_date + '_' + end_date + '_dir.nc', 
    './Coastal_Data/Op_ECMWF_airport_' + start_date + '_' + end_date + '_mag.nc', 
    'Op_ECMWF', 12, coastal_stations, dates
)

Convert to cartestian coordinates. Note that by default, wind directions are set to nan wherever wind magnitudes are zero. Given that the zonal and meridional winds $u$ and $v$ are derived from magnitude $a$ and direction $\theta$ according to $(u,v) = \left( -a\sin\theta, -a\cos\theta \right)$, these nan values should be swapped for zeros to ensure that the $u$ and $v$ components are not set to nan in the case of zero magnitude winds.

In [11]:
# Hard code solution to annoying inconsistency with obs data.
if (200601 in obs_mag['station_number'].values & 200601 not in obs_dir['station_number'].values):
        obs_mag = obs_mag.where(obs_mag['station_number'] != 200601). \
        dropna('station_number', how = 'all')
        
if (4100 in obs_mag['station_number'].values & 4100 not in obs_dir['station_number'].values):
        obs_mag = obs_mag.where(obs_mag['station_number'] != 4100). \
        dropna('station_number', how = 'all')

# Swap nan direction values for zeros. 
obs_dir = obs_dir.where(obs_mag != 0, 0)
off_dir = off_dir.where(off_mag != 0, 0)
ocf_dir = ocf_dir.where(ocf_mag != 0, 0)
acc_dir = acc_dir.where(acc_mag != 0, 0)
ecm_dir = ecm_dir.where(ecm_mag != 0, 0)

# Convert to cartesian coordinates and store in xarray dataset. 
u, v = polar2cartesian_met(obs_mag, obs_dir)
obs = xr.Dataset({'u' : u, 'v' : v})

u, v = polar2cartesian_met(off_mag, off_dir)
off = xr.Dataset({'u' : u, 'v' : v})

u, v = polar2cartesian_met(ocf_mag, ocf_dir)
ocf = xr.Dataset({'u' : u, 'v' : v})

u, v = polar2cartesian_met(acc_mag, acc_dir)
acc = xr.Dataset({'u' : u, 'v' : v})

u, v = polar2cartesian_met(ecm_mag, ecm_dir)
ecm = xr.Dataset({'u' : u, 'v' : v})

/Users/Ewan/anaconda3/envs/jive/lib/python3.6/site-packages/ipykernel_launcher.py:2: DeprecationWarning:

elementwise == comparison failed; this will raise an error in the future.

/Users/Ewan/anaconda3/envs/jive/lib/python3.6/site-packages/ipykernel_launcher.py:6: DeprecationWarning:

elementwise == comparison failed; this will raise an error in the future.



Interpolate three hourly ECMWF data onto an hourly grid; this is a standard practice for forecasters using ECMWF to inform the official forecast. 

In [12]:
ecm = ecm.resample(valid_start = '1H').interpolate('linear')

Next, choose the model dataset (OCF, ACCESS or ECMWF) to compare with the official forecast: the rest of this notebook will use OCF as an example. The jive function `broadcast_and_match_nan` is used to ensure there is consistency in the availability of data across the observational, official forecast and model datasets. Note the observational dataset does not have a `lead_day` dimension, but one is created for it by the `broadcast_and_match_nan` function with the values identical across each lead day.     

In [13]:
dat = acc
dat_name = 'ACCESS'

dat_alt = ecm 
dat_alt_name = 'ECMWF'

# As a quick hack swap off with ECMWF - quicker to change labels manually 
# off = ecm

obs, off, dat, dat_alt = broadcast_and_match_nan(obs, off, dat, dat_alt)

for source in [obs, off, dat, dat_alt]:
    source.dropna('station_number', how='all')

Calculate $u$ and $v$ perturbations from a one day running mean background wind.

In [14]:
for source in [obs, off, dat, dat_alt]:
    for comp in ['u', 'v']:
        background_wind = source[comp].rolling(valid_start=24,center=True).mean()
        var = f'{comp}_pert'
        source[var] = (
            source[comp] - background_wind
        )

# Daily Performance 

In this section the performance of the official and model forecasts are compared on a daily basis. First, the winds and wind perturbations for an example day are plotted as hodographs to provide physical intuition. Second, the Wind Perturbation Index $\text{WPI}$ defined [above](#daily_perturbation_index_definitions) is calculated, and plotted as a heatmap for the different hours and lead days.

## Functions ##

First, define the functions used throughout this section.

In [15]:
def format_data(data, date, station_list, lead_day=1, pert = True):
    """
    Restrict an xarray dataset and format for plotting.
    
    Args:
        data (xarray.Dataset): The xarray dataset containing the wind and wind 
            perturbation data.
        date (str): A string of the form 'yyyy/mm/dd' - for example '2018/07/01'.
        station_list (numpy.ndarray): IDs of the stations to restrict the xarray 
            dataset to.
        lead_day (int, optional): The lead day to restrict the xarray dataset
            to. Defaults to 1. 
        pert (bool, optional): Whether to use perturbation winds (True) or raw
            winds (false). Defaults to True. 
            
    Returns:
        data_x (numpy.ndarray): Zonal winds for each hour of the given day.
        data_y (numpy.ndarray): Meridional winds for each hour of the given day. 
        data_lab (numpy.ndarray): Strings to use as plot labels for each hour of
            the given day. 
    
    """
        
    year = int(date[0:4])
    month = int(date[4:6])
    day = int(date[6:8])
    
    if pert == True:
        var_u = 'u_pert'
        var_v = 'v_pert'
    else:
        var_u = 'u'
        var_v = 'v'
    
    if np.size(station_list) == 1:
        station_list = [station_list]
    focus_stations = data[var_u]['station_number'] == station_list[0]
    for i in np.arange(1,np.size(station_list)):
        focus_stations = np.logical_or(
            focus_stations,(data[var_u]['station_number'] == station_list[i])
        )
    
    focus = (
        (data[var_u]['valid_start.year'] == year) & \
        (data[var_u]['valid_start.month'] == month) & \
        (data[var_u]['valid_start.day'] == day) & \
        (data[var_u]['lead_day'] == lead_day) & \
        focus_stations
    )
    
    agg=stats.aggregate(
        data[var_u].where(focus).dropna('valid_start',how='all')\
        .dropna('station_number', how='all'),
        dims=['valid_start'], stats=['mean','std']
    )
    
    data_x=agg['mean'].values
    data_x_std=agg['std'].values

    agg=stats.aggregate(
        data[var_v].where(focus).dropna('valid_start',how='all')\
        .dropna('station_number', how='all'),
        dims=['valid_start'], stats=['mean','count','std']
    )

    data_y=agg['mean'].values
    data_y_std=agg['std'].values
    n_data=agg['count'].values.astype(int)

    # Use max as a way to extract non-nan values for the labels when at least  
    # one station has a non-nan value; mean not working for datetime64.
    data_real=xr.ufuncs.logical_not(xr.ufuncs.isnan(data[var_u]))
    agg=stats.aggregate(
        data['valid_start'].where(focus & data_real). \
        dropna('valid_start',how='all'), dims=['valid_start'], stats=['max']
    )
    data_lab=np.datetime_as_string(agg['valid_start'].values, unit='m')
    
    lab=np.empty(data_lab.shape, dtype = object)
    
    for i in np.arange(0,data_lab.size):
        lab[i] = (
            '%05.2f' % np.sqrt(data_x[i]**2+data_y[i]**2) + \
            ' kn </br>' + data_lab[i][0:10] + '</br>' + data_lab[i][11:16] + \
            ' UTC </br>' + 'n = %i' % n_data[i]
        )
    data_lab=lab
    
    return data_x, data_y, data_lab

def gen_trace(
    x,y,lab,name='data', colour='blue', symbol = 100, xaxis = 'x1', yaxis = 'y1', dash = 'line'
):
    """
    Generate the plotly trace for the given data. 
    """
    
    trace = {
        'x' : x,
        'y' : y,
        'xaxis' : xaxis,
        'yaxis' : yaxis,
        'mode' : 'lines+markers',
        'name' : name,
        'line' : {'color' : colour, 'width' : 2, 'dash' : dash},
        'marker' : {'size': 6,  'symbol' : symbol},
        'type' : 'scatter',
        'text' : lab
    }
    return trace

def gen_hour_dict(hour_start=0, hour_step=1):
    """
    Divide the hours in the day into groups and store in a dictionary.  
    """

    hour_dict=dict()

    if np.all(hour_start!=np.arange(0,24)): 
        sys.exit('hour_start must be integer between 0 and 23.')

    if np.all(hour_step!=np.array([1,2,3,4,6,12])): 
        sys.exit('hour_step must be a factor of 24, but less than 24.')

    hour_blocks=np.arange(hour_start,hour_start+24,hour_step)
    hour_mean=np.empty(hour_blocks.size)
    for i in np.arange(0,hour_blocks.size):
        hour_dict[i]=np.mod(
            np.arange(hour_blocks[i],hour_blocks[i]+hour_step),24
        )
        hour_mean[i]=np.mod(
            np.arange(hour_blocks[i],hour_blocks[i]+hour_step).mean(),24
        )
    
    return hour_dict, hour_blocks, hour_mean

def calc_wpi(obs, dat, dat_alt, off, station_list):
    np.seterr(invalid='ignore')
    
    # Create a meshgrid of the stations to average over
    X, Y = np.meshgrid(obs['station_number'], station_list)
    focus_stations=np.any(X==Y,0)
    
    # Average over stations.
    s_av = [obs, dat, dat_alt, off]
    for i in np.arange(0, len(s_av)):
        s_av[i] = s_av[i].where(s_av[i]['station_number'][focus_stations]).\
            mean(dim = 'station_number', skipna=True)
    [obs, dat, dat_alt, off] = s_av
    
    wpi_dat = np.sqrt(
        (dat['u_pert']-obs['u_pert']) ** 2 + (dat['v_pert']-obs['v_pert']) **2
    )
    wpi_dat_alt = np.sqrt(
        (dat_alt['u_pert']-obs['u_pert']) ** 2 + (dat_alt['v_pert']-obs['v_pert']) **2
    )
    wpi_off = np.sqrt(
        (off['u_pert']-obs['u_pert']) ** 2 + (off['v_pert']-obs['v_pert']) ** 2
    )

    wpi=wpi_dat - wpi_off
    wpi_alt=wpi_dat_alt - wpi_off

    wpi_dat_alt_dat = wpi_dat - wpi_dat_alt 

    wpi.name = 'wpi'
    wpi_alt.name = 'wpi_alt'
    wpi_dat.name = 'wpi_dat'
    wpi_dat_alt.name = 'wpi_dat_alt'
    wpi_off.name = 'wpi_off'
    wpi_dat_alt_dat.name = 'wpi_dat_alt_dat'

    wpi = xr.merge([wpi, wpi_alt, wpi_dat, wpi_dat_alt, wpi_off, wpi_dat_alt_dat])
    
    return [wpi, obs, dat, dat_alt, off]

def calc_wpi_stats(
    ind, start_date, end_date, hour_start=0, hour_step=1
):
    """
    Calculate WPI mean, standard deviation, confidence etc. 
    """
    
    np.seterr(invalid='ignore')
    
    # Restrict data to start and end dates
    ind = ind.sel(valid_start = slice(start_date, end_date))
    
    hour_dict, hour_blocks, hour_mean = gen_hour_dict(hour_start, hour_step)
    
    count_h=np.empty(np.array([hour_blocks.size,ind.shape[1]]))
    mean_h=np.empty(np.array([hour_blocks.size,ind.shape[1]]))
    std_h=np.empty(np.array([hour_blocks.size,ind.shape[1]]))
    confidence_h=np.empty(np.array([hour_blocks.size,ind.shape[1]]))
    # Confidence intervals accounting for temporal autocorrelation.
    t_test_confidence_eff_n_h=np.empty(np.array([hour_blocks.size,ind.shape[1]]))
    rho_h=np.empty(np.array([hour_blocks.size, ind.shape[1]]))
    rho_p_h=np.empty(np.array([hour_blocks.size,ind.shape[1]]))

    for i in np.arange(0,hour_blocks.size):
    
        hour_list = hour_dict[i]
        X, Y = np.meshgrid(ind['valid_start.hour'], hour_list)
        focus_hour = np.any(X == Y, 0)
        focus_hour = ind['valid_start'][focus_hour]

        agg = stats.aggregate(
            ind.where(focus_hour), dims=['lead_day'],
            stats=['count','mean','std', 't_test_confidence']
        )

        count_h[i,:] = agg['count'].values
        mean_h[i,:] = agg['mean'].values
        std_h[i,:] = agg['std'].values
        confidence_h[i,:] = agg['t_test_confidence'].values
        
        for l in np.arange(0,np.size(ind.lead_day)):
        
            # Calculate lag 1 autocorrelation
            t_series=np.squeeze(
                ind.where(focus_hour).dropna('valid_start', how='all')\
                .where(ind.lead_day==ind.lead_day[l]).dropna('lead_day', how='all')\
            )
            
            if np.size(t_series)==0:
                rho_h[i,l] = np.nan
                rho_p_h[i,l] = np.nan
            else:
                t_series = t_series[~np.isnan(t_series)]
                (rho, rho_p) = ss.pearsonr(t_series[1:], t_series[0:-1])

                rho_h[i,l] = rho
                rho_p_h[i,l] = rho_p
        
        count_h_p = count_h[i,:] * (1 - rho_h[i,:]) / (1 + rho_h[i,:])
        t_test_confidence_eff_n_h[i,:] = 1 - t.cdf(
            0, count_h_p - 1, loc=mean_h[i,:], scale=std_h[i,:] / np.sqrt(count_h_p)
        )
    
    # Store in xarray dataset
    dims=['hour','lead_day']
    coords={
        'hour' : hour_mean, 
        'lead_day' : ind.coords['lead_day'].values
    }
    ind_h=xr.Dataset(
        {
            'count' : (dims, count_h), 'mean' : (dims, mean_h),
            'std' : (dims, std_h), 't_test_confidence' : (dims, confidence_h),
            'rho' : (dims, rho_h), 'rho_p' : (dims, rho_p_h), 
            't_test_confidence_eff_n' : (dims, t_test_confidence_eff_n_h)
        }, 
        coords=coords
    )

    np.seterr(invalid='warn')
    
    return ind_h

def format_grouped_data(group_names, obs, dat, dat_alt, off):

    np.seterr(invalid='ignore')
    
    hInd = np.arange(0.0,24.0)
    sInd = np.arange(0, len(group_names))

    # WPI confidence for Official vs dat and Official vs dat_alt
    wpi_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_alt_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_dat_alt_dat_g=np.zeros((len(group_names), np.size(hInd)))

    # Mean WPI
    wpi_mean_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_alt_mean_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_dat_alt_dat_mean_g=np.zeros((len(group_names), np.size(hInd)))

    # Mean WPI_dat, WPI_dat_alt and WPI_Official
    wpi_dat_mean_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_dat_alt_mean_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_off_mean_g=np.zeros((len(group_names), np.size(hInd)))

    # Other WPI stats
    wpi_std_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_alt_std_g=np.zeros((len(group_names), np.size(hInd)))
    wpi_dat_alt_dat_std_g=np.zeros((len(group_names), np.size(hInd)))
    rho_g=np.zeros((len(group_names), np.size(hInd)))
    rho_p_g=np.zeros((len(group_names), np.size(hInd)))
    
    # Perturbation standard deviations
    obs_u_pert_std_g=np.zeros((len(group_names), np.size(hInd)))
    obs_v_pert_std_g=np.zeros((len(group_names), np.size(hInd)))
    dat_u_pert_std_g=np.zeros((len(group_names), np.size(hInd)))
    dat_v_pert_std_g=np.zeros((len(group_names), np.size(hInd)))
    dat_alt_u_pert_std_g=np.zeros((len(group_names), np.size(hInd)))
    dat_alt_v_pert_std_g=np.zeros((len(group_names), np.size(hInd)))
    off_u_pert_std_g=np.zeros((len(group_names), np.size(hInd)))
    off_v_pert_std_g=np.zeros((len(group_names), np.size(hInd)))

    for s in np.arange(0,len(group_names)):
        
        # Calculate spatially averaged datasets and wpi index
        [wpi_s, obs_s, dat_s, dat_alt_s, off_s] = calc_wpi(
            obs, dat, dat_alt, off, list(eval(group_names[s]))
        )
        
        wpi_h_s=calc_wpi_stats(wpi_s['wpi'], start_date, end_date)
        wpi_alt_h_s=calc_wpi_stats(wpi_s['wpi_alt'], start_date, end_date)
        wpi_dat_alt_dat_h_s=calc_wpi_stats(wpi_s['wpi_dat_alt_dat'], start_date, end_date)
        
        wpi_dat_h_s=calc_wpi_stats(wpi_s['wpi_dat'], start_date, end_date)
        wpi_dat_alt_h_s=calc_wpi_stats(wpi_s['wpi_dat_alt'], start_date, end_date)
        wpi_off_h_s=calc_wpi_stats(wpi_s['wpi_off'], start_date, end_date)
        
        obs_u_pert_s=calc_wpi_stats(obs_s['u_pert'], start_date, end_date)
        obs_v_pert_s=calc_wpi_stats(obs_s['v_pert'], start_date, end_date)
        dat_u_pert_s=calc_wpi_stats(dat_s['u_pert'], start_date, end_date)
        dat_v_pert_s=calc_wpi_stats(dat_s['v_pert'], start_date, end_date)
        dat_alt_u_pert_s=calc_wpi_stats(dat_alt_s['u_pert'], start_date, end_date)
        dat_alt_v_pert_s=calc_wpi_stats(dat_alt_s['v_pert'], start_date, end_date)
        off_u_pert_s=calc_wpi_stats(off_s['u_pert'], start_date, end_date)
        off_v_pert_s=calc_wpi_stats(off_s['v_pert'], start_date, end_date)

        obs_u_pert_std_g[s,:] = np.squeeze(
            obs_u_pert_s['std'].\
            where(obs_u_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        obs_v_pert_std_g[s,:] = np.squeeze(
            obs_v_pert_s['std'].\
            where(obs_v_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        dat_u_pert_std_g[s,:] = np.squeeze(
            dat_u_pert_s['std'].\
            where(dat_u_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        dat_v_pert_std_g[s,:] = np.squeeze(
            dat_v_pert_s['std'].\
            where(dat_v_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        dat_alt_u_pert_std_g[s,:] = np.squeeze(
            dat_alt_u_pert_s['std'].\
            where(dat_alt_u_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        dat_alt_v_pert_std_g[s,:] = np.squeeze(
            dat_alt_v_pert_s['std'].\
            where(dat_alt_v_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        off_u_pert_std_g[s,:] = np.squeeze(
            off_u_pert_s['std'].\
            where(off_u_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        off_v_pert_std_g[s,:] = np.squeeze(
            off_v_pert_s['std'].\
            where(off_v_pert_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )

        wpi_g[s,:] = np.squeeze(
            wpi_h_s['t_test_confidence_eff_n'].\
            where(wpi_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_alt_g[s,:] = np.squeeze(
            wpi_alt_h_s['t_test_confidence_eff_n'].\
            where(wpi_alt_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_dat_alt_dat_g[s,:] = np.squeeze(
            wpi_dat_alt_dat_h_s['t_test_confidence_eff_n'].\
            where(wpi_dat_alt_dat_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_mean_g[s,:] = np.squeeze(
            wpi_h_s['mean'].\
            where(wpi_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_alt_mean_g[s,:] = np.squeeze(
            wpi_alt_h_s['mean'].\
            where(wpi_alt_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_dat_alt_dat_mean_g[s,:] = np.squeeze(
            wpi_dat_alt_dat_h_s['mean'].\
            where(wpi_dat_alt_dat_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_std_g[s,:] = np.squeeze(
            wpi_h_s['std'].\
            where(wpi_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_alt_std_g[s,:] = np.squeeze(
            wpi_alt_h_s['std'].\
            where(wpi_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_dat_alt_dat_std_g[s,:] = np.squeeze(
            wpi_dat_alt_dat_h_s['std'].\
            where(wpi_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        
        rho_g[s,:] = np.squeeze(
            wpi_h_s['rho'].\
            where(wpi_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        rho_p_g[s,:] = np.squeeze(
            wpi_h_s['rho_p'].\
            where(wpi_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_dat_mean_g[s,:] = np.squeeze(
            wpi_dat_h_s['mean'].\
            where(wpi_dat_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_dat_alt_mean_g[s,:] = np.squeeze(
            wpi_dat_alt_h_s['mean'].\
            where(wpi_dat_alt_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
        wpi_off_mean_g[s,:] = np.squeeze(
            wpi_off_h_s['mean'].\
            where(wpi_off_h_s.lead_day==1).\
            dropna(dim = 'lead_day', how='any').values
        )
    
    wpi_g = np.round(wpi_g * 100).astype(int)
    wpi_alt_g = np.round(wpi_alt_g * 100).astype(int)
    wpi_dat_alt_dat_g = np.round(wpi_dat_alt_dat_g * 100).astype(int)
    
    np.seterr(invalid='warn')
    
    return [wpi_g, wpi_alt_g, wpi_dat_alt_dat_g, wpi_mean_g, wpi_alt_mean_g, wpi_dat_alt_dat_mean_g, 
            wpi_dat_mean_g, wpi_dat_alt_mean_g, wpi_off_mean_g, wpi_std_g, rho_g, rho_p_g,
            obs_u_pert_std_g, obs_v_pert_std_g, dat_u_pert_std_g, dat_v_pert_std_g,
            dat_alt_u_pert_std_g, dat_alt_v_pert_std_g, off_u_pert_std_g, off_v_pert_std_g]

def plot_group_data_scorecards(Z, group_names, group_lab, fn_prefix = 'group'):

    hInd = np.arange(0.0,24.0)
    sInd = np.arange(0, len(group_names))

    # Create labels for heatmap.
    X, Y = np.meshgrid(hInd, sInd)

    z = [source.flatten() for source in Z]

    z_lab = [z[0].astype(str), z[1].astype(str), z[2].astype(str)]

    # Convert label values to strings
    for i in np.arange(3, len(z)):
        z_lab_i = np.empty(np.size(z[i]))
        for j in np.arange(0,np.size(z[0])):
            z_lab_i[j] = "{:.1f}".format(z[i][j])
        z_lab = z_lab + [z_lab_i.astype('U21')]
        
    z_dat_dat_alt_u_std_min = np.min(np.concatenate((z[14], z[16])))
    z_dat_dat_alt_u_std_max = np.max(np.concatenate((z[14], z[16])))
    z_dat_dat_alt_v_std_min = np.min(np.concatenate((z[15], z[17])))
    z_dat_dat_alt_v_std_max = np.max(np.concatenate((z[15], z[17])))
    wpi_abs_max = np.ceil(np.max(np.abs(np.concatenate((z[3], z[4], z[5]))))*10)/10

    z_min = [
        0, 0, 0, -wpi_abs_max, -wpi_abs_max, -wpi_abs_max,
        np.floor(np.min(np.abs(z[6]))*10)/10, np.floor(np.min(np.abs(z[7]))*10)/10, np.floor(np.min(np.abs(z[8]))*10)/10, np.floor(np.min(np.abs(z[9]))*10)/10, -1.0, 0.0,
        np.floor(np.min(z[12])*10)/10, np.floor(np.min(z[13])*10)/10, np.floor(z_dat_dat_alt_u_std_min*10)/10, np.floor(z_dat_dat_alt_v_std_min*10)/10, 
        np.floor(z_dat_dat_alt_u_std_min*10)/10, np.floor(z_dat_dat_alt_v_std_min*10)/10, np.floor(np.min(z[18])*10)/10, np.floor(np.min(z[19])*10)/10
            ]
    z_min = z_min + [0] * 8  
    z_max = [
        100, 100, 100, wpi_abs_max, wpi_abs_max, wpi_abs_max,
        np.ceil(np.max(np.abs(z[6]))*10)/10, np.ceil(np.max(np.abs(z[7]))*10)/10, 
        np.ceil(np.max(np.abs(z[8]))*10)/10, np.ceil(np.max(np.abs(z[9]))*10)/10,
        1.0, 1.0,
        np.ceil(np.max(z[12])*10)/10, np.ceil(np.max(z[13])*10)/10, np.ceil(z_dat_dat_alt_u_std_max*10)/10, np.ceil(z_dat_dat_alt_v_std_max*10)/10, 
        np.ceil(z_dat_dat_alt_u_std_max*10)/10, np.ceil(z_dat_dat_alt_v_std_max*10)/10, np.ceil(np.max(z[18])*10)/10, np.ceil(np.max(z[19])*10)/10,
    ]
    for i in np.arange(12,len(z)):
        z_max = z_max + [np.max(np.abs(z[i]))]
    
    bar_lab = [
        '[%]', '[%]', '[%]', '[kn]', '[kn]', '[kn]', '[kn]', '[kn]', '[kn]', '[kn]', 
        'Correlation Coefficient [-]', 'Probability [-]'
    ]
    bar_lab = bar_lab + ['kn'] * 8

    title = [
        'Percentage Chance that Official is Better than ' + dat_name, 
        'Percentage Chance that Official is Better than ' + dat_alt_name, 
        'Percentage Chance that ' + dat_alt_name + ' is Better than ' + dat_name, 
        'Mean Official vs ' + dat_name + ' WPI', 'Mean Official vs ' + dat_alt_name + ' WPI', 
        'Mean ' + dat_alt_name + ' vs ' + dat_name + ' WPI', 
        'Mean WPI_' + dat_name, 'Mean WPI_' + dat_alt_name,
        'Mean WPI_Official', 'Standard Deviation of WPI (Official vs ' + dat_name + ')', 
        'Lag 1 Autocorrelation (Official vs ' + dat_name + ')', 
        'Autocorrelation p-Value (Official vs ' + dat_name + ')',
        'Standard Deviation of Observed Zonal Perturbations',
        'Standard Deviation of Observed Meridional Perturbations',
        'Standard Deviation of ' + dat_name + ' Zonal Perturbations',
        'Standard Deviation of ' + dat_name + ' Meridional Perturbations',
        'Standard Deviation of ' + dat_alt_name + ' Zonal Perturbations',
        'Standard Deviation of ' + dat_alt_name + ' Meridional Perturbations',
        'Standard Deviation of Official Zonal Perturbations',
        'Standard Deviation of Official Meridional Perturbations',
    ]

    file_name = [
        fn_prefix + '_comp_wpi_', fn_prefix + '_comp_wpi_alt', fn_prefix + '_comp_wpi_dat_alt_dat',
        fn_prefix + '_comp_wpi_mean_', fn_prefix + '_comp_wpi_alt_mean_', 
        fn_prefix + '_comp_wpi_dat_alt_dat_mean_', 
        fn_prefix + '_comp_wpi' + dat_name + 'mean_', 
        fn_prefix + '_comp_wpi' + dat_alt_name + 'mean_',
        fn_prefix + '_comp_wpi' + dat_alt_name + 'mean_',
        fn_prefix + '_comp_wpi_official_mean_', fn_prefix + '_comp_wpi_std_', fn_prefix + '_comp_wpi_rho_', 
        fn_prefix + '_comp_wpi_rho_p_',
    ]
    for source in ['Observed', dat_name, dat_alt_name, 'Official']:
        file_name = file_name + [fn_prefix + 'u_pert_std_' + source, fn_prefix + 'v_pert_std_' + source]

    color_scale = [
        'RdBu', 'RdBu', 'RdBu', 'RdBu', 'RdBu', 'RdBu', 'Reds', 'Reds', 'Reds', 'Reds', 'RdBu', 'Reds'
    ]
    color_scale = color_scale + ['Reds'] * 8

    x = X.flatten()
    y = Y.flatten()
    
    for i in np.arange(0,len(Z)):

        # Create heat map trace.
        trace_heat = {
            'z' : Z[i],
            'zmin' : z_min[i], 
            'zmax' : z_max[i], 
            'x' : hInd,
            'y' : sInd,
            'type' : 'heatmap',
            'colorbar' : {
                'title' : bar_lab[i],
                'titleside' : 'right',
                'thickness' : 15,
                'nticks' : 20
            },
            'colorscale' : color_scale[i],
            'hoverinfo' : 'none',
        }

        # Use a scatterplot trace for the labels. 
        trace_label = {
            'x' : x,
            'y' : y,
            'text' : z_lab[i],
            'textfont' : {
                'size'  : 8,
            },
            'type' : 'scatter',
            'mode' : 'text',
            'name' : bar_lab[i],
        }

        layout = go.Layout(
            title = title[i],
            width = 540,
            height = 230,
            xaxis = dict(
                title = 'Hour [UTC]', showgrid = False, range = [-0.5,23.5],
                autotick = False, dtick = 4,
            ),
            yaxis = go.YAxis(
                tickmode = 'array',
                ticktext = group_lab,
                tickvals=sInd, range = [-0.5, len(group_names) - 0.5],
                title = 'Station', showgrid = False, 
            ),
            hovermode = 'closest',
            margin = {
                't' : 40, 'l' : 140
            },
            font = {
                'family' : 'Times New Roman', 'size' : '10', 'color' : 'black',
            },
        )

        fig = {
            'data': [trace_heat, trace_label], 
            'layout': layout
        }

        iplot(fig)

        file_name_i = file_name[i] + start_date + '_' + end_date + '_' + dat_name

        if save_plot:
            plotly.offline.plot(
                fig,  filename=file_name_i + '.html', image='svg', output_type='file', 
                image_width=540, image_height=230, 
                image_filename=file_name_i + '.svg'
            )
        
    return

## Hodographs

Generate hodographs (plots showing the evolution of winds with time) for both the raw winds and the wind perturbations. By default, hodographs for the 1st July 2017 at Darwin Aiport are considered. If multiple station IDs are input, data is first averaged over these stations. Note this is done _before_ calculating $\text{WPI}$ values: if this averaging were not performed the variance of the sampling distribution of the mean $\text{WPI}$ for each hour would be artificially reduced as data is highly correlated across nearby stations.        

In [19]:
# Specify date as a string in yyyy/mm/dd format
if season == 'austral_summer':
    date = '20171201'
elif season == 'austral_winter':
    date = '20180703'
# Specify lead day
lead_day = 1
# specify station group
s_group = 'nt_coastal'
# Specify stations as a numpy array of station ID numbers.
station_list = np.array(list(eval(s_group)))
save_plot = False
 
# Generate plotly traces and store in dictionaries.
trace = dict()
trace_pert = dict()

for source in [
    ['obs', 'Obs.', 'green'],
    ['off', 'Official', 'red'], 
    ['dat', dat_name, 'blue'],
    ['dat_alt', dat_alt_name, 'orange']
]:
    x, y, lab = format_data(
        eval(source[0]), date, station_list, lead_day, pert = False
    )
    trace[source[0]] = gen_trace(x, y, lab, source[1], source[2], 0)
    x, y, lab = format_data(
        eval(source[0]), date, station_list, lead_day, pert = True)
    trace_pert[source[0]] = gen_trace(
        x, y, lab, source[1] + ' Pert.', source[2], 0
    )
    
# Plot using plotly.
fig = tools.make_subplots(
    rows=1, cols=2, 
    subplot_titles=('a) Winds', 'b) Wind Perturbations'), 
    specs = [[{}, {}]],
    print_grid=False
)

for source in ['obs', 'off', 'dat', 'dat_alt']:
    fig.append_trace(trace[source], 1, 1)
    fig.append_trace(trace_pert[source], 1, 2)
    
# Add axis titles
fig['layout']['xaxis1'].update(title='u [kn]')
fig['layout']['yaxis1'].update(title='v [kn]', scaleanchor = 'x', scaleratio=1)
fig['layout']['xaxis2'].update(title='u [kn]')
fig['layout']['yaxis2'].update(title='v [kn]', scaleanchor = 'x2', scaleratio=1)

fig['layout'].update(
    title = 'Wind Hodographs ' + date, width = 700, height = 400, 
    hovermode = 'closest',
    font=dict(family='Times New Roman', size=12, color='black'),
    legend=dict(orientation="h", x=1.2, y=-.3),
    yaxis=dict(scaleanchor="x", scaleratio=1),
)

iplot(fig)

if save_plot:
    plotly.offline.plot(
        fig,  filename='daily_winds.html', image='svg', output_type='file', 
        image_width=700, image_height=400, 
        image_filename='daily_winds_' + s_group + '_' + start_date + '_' + 
            end_date + '_' + dat_name
    )

A land-sea breeze signal is clearly evident in above hodographs. In figure a), the raw wind hodographs show offshore winds for OCF for the entire day. The official forecast gives an onshore wind peaking at 14 kn at 08:00 UTC. Observations are mostly somewhere in between, with a weak onshore wind of 5.40 kn also peaking at 08:00 UTC. Notice that the winds generally evolve in a counter clockwise direction demonstrating the effect of the Coriolis force which in the southern hemisphere turns the land and sea breezes to the left (e.g [https://www.doi.org/10.1029/2004GL022139](https://www.doi.org/10.1029/2004GL022139).) Figure b) reveals the land-sea processes more clearly, with land-sea breeze _perturbations_ clear in all three datasets, including OCF. When thinking about land-sea breeze signals in this way - as perturbations from a daily mean background wind - it is worth noting that theory suggests that in the tropics background winds have a non-trivial effect on land-sea breeze perturbations (e.g [https://doi.org/10.1175/2008JAS2851.1](https://doi.org/10.1175/2008JAS2851.1).) 

## Soundings

Plot the Perth Airport mid-level sounding hodographs.

In [17]:
height_06081200 = np.array([20, 147, 155, 799, 1208, 1492, 1569, 1607, 2360, 2423])
dir_06081200 = np.array([10, 0, 360, 325, 290, 305, 308, 310, 307, 307])
speed_06081200 = np.array([7, 12, 12, 14, 13, 16, 18, 19, 21, 21])
u_06081200, v_06081200 = polar2cartesian_met(speed_06081200, dir_06081200)

height_06090000 = np.array([20, 126, 372, 573, 778, 805, 1050, 1417, 1475, 2434])
dir_06090000 = np.array([15, 10, 355, 340, 325, 320, 310, 300, 300, 291])
speed_06090000 = np.array([12, 22, 32, 30, 28, 28, 20, 26, 28, 32])
u_06090000, v_06090000 = polar2cartesian_met(speed_06090000, dir_06090000)

height_06091200 = np.array([20, 60, 109, 725, 771, 1235, 1244, 1474, 2201, 2684])
dir_06091200 = np.array([5, 345, 345, 320, 320, 310, 310, 305, 290, 295])
speed_06091200 = np.array([11, 11, 17, 37, 38, 36, 36, 35, 34, 45])
u_06091200, v_06091200 = polar2cartesian_met(speed_06091200, dir_06091200)

perth_trace_06081200 = gen_trace(
    u_06081200, v_06081200, height_06081200.astype(str), 
    '8 June 2018 12:00 UTC', 'rgb(25,25,25)', 0, dash = 'line'
)
perth_trace_06081200['mode'] = 'lines+markers+text'
perth_trace_06081200['text'] = height_06081200.astype(str)
perth_trace_06081200['textposition'] = 'top center'
    
perth_trace_06090000 = gen_trace(
    u_06090000, v_06090000, height_06090000.astype(str), 
    '9 June 2018 00:00 UTC', 'rgb(75,75,75)', 1, dash = 'dash'
)
perth_trace_06090000['mode'] = 'lines+markers+text'
perth_trace_06090000['text'] = height_06090000.astype(str)
perth_trace_06090000['textposition'] = 'top center'

perth_trace_06091200 = gen_trace(
    u_06091200, v_06091200, height_06091200.astype(str), 
    '9 June 2018 12:00 UTC', 'rgb(125,125,125)', 2, dash = 'dot'
)
perth_trace_06091200['mode'] = 'lines+markers+text'
perth_trace_06091200['text'] = height_06091200.astype(str)
perth_trace_06091200['textposition'] = 'top center'

layout=go.Layout()
fig = {
    'data': [perth_trace_06081200, perth_trace_06090000, perth_trace_06091200], 
    'layout': layout
}
fig['layout'].update(
    title = 'Perth Airport Wind Profiles', width = 400, height = 450, 
    hovermode = 'closest',
    font=dict(family='Times New Roman', size=12, color='black'),
    legend=dict(orientation="h", x=1.2, y=-.3),
    yaxis=dict(scaleanchor="x", scaleratio=1)
)

# Add axis titles
fig['layout']['xaxis'].update(title='u [kn]')
fig['layout']['yaxis'].update(title='v [kn]', scaleanchor = 'x', scaleratio=1)

iplot(fig)

if save_plot:
    plotly.offline.plot(
        fig,  filename='perth_sounding.html', image='svg', output_type='file', 
        image_width=400, image_height=450, 
        image_filename='perth_sounding_' + start_date + '_' + 
            end_date + '_' + dat_name
    )

In [18]:
height_07021200 = np.array([20, 147, 155, 799, 1208, 1492, 1569, 1607, 2360, 2423])
dir_07021200 = np.array([10, 0, 360, 325, 290, 305, 308, 310, 307, 307])
speed_07021200 = np.array([7, 12, 12, 14, 13, 16, 18, 19, 21, 21])
u_07021200, v_07021200 = polar2cartesian_met(speed_07021200, dir_07021200)

height_07030000 = np.array([20, 126, 372, 573, 778, 805, 1050, 1417, 1475, 2434])
dir_07030000 = np.array([15, 10, 355, 340, 325, 320, 310, 300, 300, 291])
speed_07030000 = np.array([12, 22, 32, 30, 28, 28, 20, 26, 28, 32])
u_07030000, v_07030000 = polar2cartesian_met(speed_07030000, dir_07030000)

height_07031200 = np.array([20, 60, 109, 725, 771, 1235, 1244, 1474, 2201, 2684])
dir_07031200 = np.array([5, 345, 345, 320, 320, 310, 310, 305, 290, 295])
speed_07031200 = np.array([11, 11, 17, 37, 38, 36, 36, 35, 34, 45])
u_07031200, v_07031200 = polar2cartesian_met(speed_07031200, dir_07031200)

darwin_trace_07021200 = gen_trace(
    u_07021200, v_07021200, height_07021200.astype(str), 
    '2 July 2018 12:00 UTC', 'rgb(25,25,25)', 0, dash = 'line'
)
darwin_trace_07021200['mode'] = 'lines+markers+text'
darwin_trace_07021200['text'] = height_07021200.astype(str)
darwin_trace_07021200['textposition'] = 'top center'
    
darwin_trace_07030000 = gen_trace(
    u_07030000, v_07030000, height_07030000.astype(str), 
    '3 July 2018 00:00 UTC', 'rgb(75,75,75)', 1, dash = 'dash'
)
darwin_trace_07030000['mode'] = 'lines+markers+text'
darwin_trace_07030000['text'] = height_07030000.astype(str)
darwin_trace_07030000['textposition'] = 'top center'

darwin_trace_07031200 = gen_trace(
    u_07031200, v_07031200, height_07031200.astype(str), 
    '9 June 2018 12:00 UTC', 'rgb(125,125,125)', 2, dash = 'dot'
)
darwin_trace_07031200['mode'] = 'lines+markers+text'
darwin_trace_07031200['text'] = height_07031200.astype(str)
darwin_trace_07031200['textposition'] = 'top center'

layout=go.Layout()
fig = {
    'data': [darwin_trace_07021200, darwin_trace_07030000, darwin_trace_07031200], 
    'layout': layout
}
fig['layout'].update(
    title = 'Darwin Airport Wind Profiles', width = 400, height = 450, 
    hovermode = 'closest',
    font=dict(family='Times New Roman', size=12, color='black'),
    legend=dict(orientation="h", x=1.2, y=-.3),
    yaxis=dict(scaleanchor="x", scaleratio=1)
)

# Add axis titles
fig['layout']['xaxis'].update(title='u [kn]')
fig['layout']['yaxis'].update(title='v [kn]', scaleanchor = 'x', scaleratio=1)

iplot(fig)

if save_plot:
    plotly.offline.plot(
        fig,  filename='darwin_sounding.html', image='svg', output_type='file', 
        image_width=400, image_height=450, 
        image_filename='darwin_sounding_' + start_date + '_' + 
            end_date + '_' + dat_name
    )

## Calculate WPI

Calculate the $\text{WPI}$ index and the mean for each hour and lead day. Use the Jive `aggregate` function to work out the probability that the mean value is greater than zero. Note that `aggregate` achieves this by assuming the sampling distribution of the mean follows a $t$-distrubution. This is assumption is satisfied when $\text{WPI}$ is normally distributed. An example $\text{WPI}$ sampling distribution is considered in the [appendix](#wpi_sampling_distribution).

Plot the confidence that $\text{WPI} > 0$ as a scorecard heatmap. 

In [18]:
# Specify start and end dates for calculating WPI statistics.
if season == 'austral_winter':
    start_date = '20180601'
    end_date = '20180831'
elif season == 'austral_summer':
    start_date = '20171201'
    end_date = '20180228'
    
# Specify stations as a numpy array of station ID numbers.
station_list = np.array(list(wa_coastal_north))

wpi_h = calc_wpi(obs, dat, dat_alt, off, station_list)[0]
wpi_h = calc_wpi_stats(wpi_h['wpi'], start_date, end_date)

wpi_confidence = wpi_h['t_test_confidence_eff_n'].dropna(dim = 'lead_day', how='any')

hInd = wpi_confidence.hour.values
lInd = wpi_confidence.lead_day.values

# Create labels for heatmap.
X, Y = np.meshgrid(hInd, lInd)
Z = np.round(wpi_confidence.values.T*100).astype(int)

x = X.flatten()
y = Y.flatten()
z = Z.flatten()

z_lab = z.astype(str)

# Create heat map trace.
trace_heat = {
    'z' : Z,
    'zmin' : 0, 
    'zmax' : 100, 
    'x' : hInd,
    'y' : lInd,
    'type' : 'heatmap',
    'colorbar' : {
        'title' : 'Percentage Chance',
        'titleside' : 'right',
        'tickvals' : [0, 20, 40, 60, 80, 100],
        'thickness' : 15,
    },
    'hoverinfo' : 'none',
}

# Use a scatterplot trace for the labels. 
trace_label = {
    'x' : x,
    'y' : y,
    'text' : z_lab,
    'type' : 'scatter',
    'mode' : 'text',
    'name' : 'Chance (%)',
}

layout = {
    'title' : 'Percentage Chance that Official is Better than ' + dat_name,
    'width' : 900,
    'height' : 400,
    'xaxis' : {
        'title' : 'Hour [UTC]', 'showgrid' : False, 'range' : [-0.5,23.5],
        'autotick' : False, 'dtick' : 4,
    },
    'yaxis' : {
        'title' : 'Lead Day', 'showgrid' : False, 
        'autotick' : False, 'dtick' : 1,
    },
    'hovermode': 'closest',
    'margin' : {
        't' : 80
    },
    'font' : {
        'family' : 'Times New Roman', 'size' : '12', 'color' : 'black',
    },
}

fig = {
    'data': [trace_heat, trace_label], 
    'layout': layout
}

iplot(fig)

if save_plot:
    plotly.offline.plot(
        fig,  filename='wpi.html', image='svg', output_type='file', 
        image_width=600, image_height=280, 
        image_filename='wpi_' + season + '_' + dat_name
    )

The scorecard indicates that the official forecast generally outperforms OCF with 90% confidence at 01:00, 02:00 and 07:00 UTC (10:30, 11:30 and 16:30 local time), with two caveats. 
1. For lead days 3-5 confidence at 01:00 and 02:00 UTC drops below 80%. 
2. For lead days 5-7 the official forcast also outperforms OCF at 06:00 and 08:00 UTC with at least 90%, except at 06:00 UTC for lead day 7, where confidence drops to 80%.     

One explanation for the superiority of the official forecast at 01:00 and 02:00 UTC is that forecasters typically edit model guidance after sunrise to account for the mixing down of gradient level winds through the boundary layer as boundary layer instability grows throughout the morning. The superiority of the official forecast at these times may indicate that OCF is not simulating boundary layer mixing processes correctly. The fact that OCF regains superiority at 03:00, 04:00 and 05:00 UTC may indicate that mixing processes occur in OCF, they just occur too late. 

The superiority of the official forecast at 07:00 UTC likely reflects the success of sea-breeze edits performed by forecasters at this time. The superiority of the official forecast at the additional times of 06:00 and 08:00 UTC for lead days 5-7 may reflect the fact that lead days 1-4 and 5-7 are handled by different forecasters acting in different roles.  

## Time Series

In [67]:
# Specify stations as a numpy array of station ID numbers. 
station_list = np.array(list(nt_coastal))

hour_ts = 23
lead_day_ts = 1

wpi_h = calc_wpi(obs, dat, dat_alt, off, station_list)[0]
wpi_s = wpi_h.sel(valid_start = slice(start_date, end_date))
wpi_s = wpi_s.where(wpi_s['valid_start.hour'] == hour_ts).dropna(dim = 'valid_start', how = 'all')\
                .where(wpi_s['lead_day'] == lead_day_ts).dropna(dim = 'lead_day', how = 'all')

dates_data = np.squeeze(wpi_s['valid_start'].where(wpi_s['valid_start.hour'] == hour_ts)\
                        .dropna(dim = 'valid_start', how = 'all').values)
dates_data = dates_data.astype(str)
dates_label = np.empty(np.size(dates_data), dtype = '<U21')
for i in np.arange(0,np.size(dates_data)):
    dates_label[i] = dates_data[i][0:10]

trace_list = []
variables = ['wpi', 'wpi_alt', 'wpi_dat_alt_dat', 'wpi_dat', 'wpi_dat_alt', 'wpi_off']
titles = [
    'Official vs ' + dat_name + ' WPI', 'Official vs ' + dat_alt_name + ' WPI', 
    dat_alt_name + ' vs ' + dat_name + ' WPI', 'WPI_' + dat_name, 'WPI_' + dat_alt_name, 'WPI_Official'
]
         
for i in np.arange(0,np.size(variables)):
    trace = {
        'x' : dates_label,
        'y' : np.squeeze(wpi_s[variables[i]].values),
        'type' : 'scatter',
        'mode' : 'lines+markers',
        'marker' : {'size': 4,  'symbol' : 0},
        'name' : titles[i],
        'line' : {'width' : 1.5,},
    }
    trace_list = trace_list + [trace]

fig = tools.make_subplots(rows=2, cols=1)

for trace in trace_list[0:3]:
    fig.append_trace(trace, 1, 1)
        
for trace in trace_list[3:]:
    fig.append_trace(trace, 2, 1)
    
fig['layout'].update(
    height=600, width=700, title='WPI Time Series ' + str(hour_ts) + ' UTC', 
    hovermode = 'closest', font = {'family' : 'Times New Roman', 'size' : '12', 'color' : 'black',},
    xaxis1 = dict(
        range = [dates_label[0], dates_label[-1]],
        tick0 = dates_label[0], dtick = 7*86400000.0,
        tickformat = '%B %e'
    ),
    yaxis1 = go.YAxis(
        title = 'kn',
    ),
    xaxis2 = dict(
        title = 'Date',
    ),
    yaxis2 = go.YAxis(
        title = '[kn]',
    ),
    legend=dict(orientation="h", x=1.2, y=-.3),
)

iplot(fig)

file_name = 'wpi_time_series' + '_' + str(hour_ts) + '_' + start_date + '_' + end_date + '_' + dat_name

if save_plot:
    plotly.offline.plot(
        fig,  filename = file_name + '.html', image='svg', output_type='file', 
        image_width=700, image_height=600, 
        image_filename = file_name + '.svg'
    )

This is the format of your plot grid:
[ (1,1) x1,y1 ]
[ (2,1) x2,y2 ]



## Airport Comparison

In [20]:
airport_data = format_grouped_data(airport_names, obs, dat, dat_alt, off)

In [21]:
plot_group_data_scorecards(airport_data, airport_names, airport_station_list_lab, 'airport')

## Airport Group Comparison

In [22]:
airport_grouped_data = format_grouped_data(airport_station_group_names, obs, dat, dat_alt, off)

In [23]:
plot_group_data_scorecards(airport_grouped_data, airport_station_group_names, airport_station_list_lab, 'airport')

## State Comparison

In [24]:
coastal_grouped_data = format_grouped_data(coastal_station_group_names, obs, dat, dat_alt, off)

In [47]:
plot_group_data_scorecards(coastal_grouped_data, coastal_station_group_names, coastal_station_group_labels, 'coastal')

# Climatological Performance

In this section the performance of the official and model forecasts are compared on a climatological basis. First, the mean winds and mean wind perturbations over the climatological time period (in this example the winter months of 2017) are plotted as hodographs to provide physical intuition. Second, the Climatological Wind Perturbation Index $\text{CWPI}$ defined [above](#climatological_perturbation_index_definitions) is calculated, and plotted as a heatmap for the different hours and lead days.

## Functions

Define the functions used throughout this section. 

In [50]:
def gen_composite(
    data, station_list, start_date, end_date, hour_start=0, hour_step=1
):
    """
    Aggregate data in hourly intervals and calculate means.
    """
    
    np.seterr(invalid='ignore')
    
    # Restrict data to start and end dates
    data = data.sel(valid_start = slice(start_date, end_date))
    
    # Create a meshgrid of the stations to average over
    X, Y = np.meshgrid(data['station_number'], station_list)
    focus_stations=np.any(X==Y,0)
    
    # Average over stations. Do this before calculating statistics to account 
    # for spatial correlation. 
    data = data.where(data['station_number'][focus_stations]).\
        mean(dim = 'station_number', skipna=True)
    
    hour_dict, hour_blocks, hour_mean = gen_hour_dict(hour_start, hour_step)
    
    u_pert_h=np.empty(np.array([hour_blocks.size,data['u_pert'].shape[1]]))
    v_pert_h=np.empty(np.array([hour_blocks.size,data['u_pert'].shape[1]]))
    n_pert_h=np.empty(np.array([hour_blocks.size,data['u_pert'].shape[1]]))
    u_std_pert_h=np.empty(
        np.array([hour_blocks.size, data['u_pert'].shape[1]])
    )
    v_std_pert_h=np.empty(
        np.array([hour_blocks.size, data['u_pert'].shape[1]])
    ) 
    
    for i in np.arange(0,hour_blocks.size):
    
        hour_list=hour_dict[i]
        X, Y = np.meshgrid(data['valid_start.hour'],hour_list)
        focus_hour=np.any(X==Y,0)
        focus_hour=data['valid_start'][focus_hour]

        agg=stats.aggregate(
            data['u_pert'].where(focus_hour), dims=['lead_day'], 
            stats=['mean','std']
        )

        u_pert_h[i,:]=agg['mean'].values
        u_std_pert_h[i,:]=agg['std'].values

        agg=stats.aggregate(
            data['v_pert'].where(focus_hour), dims=['lead_day'], 
            stats=['count','mean','std']
        )

        v_pert_h[i,:]=agg['mean'].values
        v_std_pert_h[i,:]=agg['std'].values
        n_pert_h[i,:]=agg['count'].values
    
    # Store in xarray dataset
    dims=['hour','lead_day']
    coords={'hour':hour_mean, 'lead_day':data.coords['lead_day'].values}     
    data_h=xr.Dataset(
        {'u_pert' : (dims, u_pert_h), 'v_pert' : (dims, v_pert_h),
        'count' : (dims, n_pert_h), 'u_pert_std' : (dims, u_std_pert_h),
        'v_pert_std' : (dims, v_std_pert_h)}, coords=coords
    )
    
    np.seterr(invalid='warn')
    
    return data_h

def format_composite(data,lead_day=1):
    """
    Format the aggregated data for plotting.
    """
   
    np.seterr(invalid='ignore')

    data_x=np.squeeze(data['u_pert'].where(data['lead_day']==lead_day). \
                     dropna('lead_day', how='all').values)
    data_y=np.squeeze(data['v_pert'].where(data['lead_day']==lead_day). \
                     dropna('lead_day', how='all').values)
    data_time=np.squeeze(data['hour'].where(data['lead_day']==lead_day). \
                       dropna('lead_day', how='all').values)
    data_count=np.squeeze(data['count'].where(data['lead_day']==lead_day). \
                       dropna('lead_day', how='all').values)
    data_x_std=np.squeeze(data['u_pert_std'].where(data['lead_day']==lead_day). \
                       dropna('lead_day', how='all').values)
    data_y_std=np.squeeze(data['v_pert_std'].where(data['lead_day']==lead_day). \
                       dropna('lead_day', how='all').values)
    
    # Format labels
    minutes,hours=np.modf(data_time)
    minutes=minutes*60
    data_lab=np.empty(data_time.shape, dtype = object)
    for i in np.arange(0,data_time.size):
        data_lab[i] = (
            '%05.2f' % np.sqrt(data_x[i]**2+data_y[i]**2) + ' kn </br>' + \
            '%02d' % hours[i] + ':' + '%02d' % minutes[i] + ' UTC </br>' + \
            'n = %i </br>' % data_count[i] + \
            's = (%05.2f ' % data_x_std[i] + ', %05.2f' % data_y_std[i] + ')'
        )
    
    np.seterr(invalid='warn')
    
    return data_x, data_y, data_lab

def resample(data, n=None):
    """
    Resample for the purposes of bootstrapping.
    """
    
    np.seterr(invalid='ignore')
    
    if n == None:
        n = data.size
        
    if data.size <= 1:
        resampled_data = data
    else:
        resample_indices = np.floor(np.random.rand(n)*data.size).astype(int)
        resampled_data = data[resample_indices]
        
    np.seterr(invalid='warn')
    
    return resampled_data

def resample_wind_data(
    data, start_date, end_date, station_list, hour, lead_day=1, N=1000
):
    """
    Caclulate resampled mean winds. 
    """
    
    np.seterr(invalid='ignore')

    # Restrict data to start and end dates
    data = data.sel(valid_start = slice(start_date, end_date))
    
    # Create a meshgrid of the stations to average over
    X, Y = np.meshgrid(data['station_number'], station_list)
    focus_stations=np.any(X==Y,0)
    
    # Average over stations. Do this before calculating statistics to account 
    # for spatial correlation. 
    data = data.where(data['station_number'][focus_stations]).\
        mean(dim = 'station_number', skipna=True)
    
    data_resample_u = np.empty(N)
    data_resample_v = np.empty(N)

    u = np.squeeze(
        data['u_pert'].where(data['lead_day'] == lead_day). \
        where(data['valid_start.hour'] == hour). \
        dropna('valid_start', how='all'). \
        dropna('lead_day', how='all').values
    )
    
    v = np.squeeze(
        data['v_pert'].where(data['lead_day'] == lead_day). \
        where(data['valid_start.hour'] == hour). \
        dropna('valid_start', how='all'). \
        dropna('lead_day', how='all').values
    )
        
    # I expect to see RuntimeWarnings in this block when averaging nan values
    with warnings.catch_warnings():
        warnings.simplefilter("ignore", category=RuntimeWarning)
        for i in np.arange(0,N):
            data_resample_u[i]=np.nanmean(resample(u))
            data_resample_v[i]=np.nanmean(resample(v))
    
    np.seterr(invalid='warn')
    
    return data_resample_u, data_resample_v

def clim_index_dist(
    obs, data1, data2, N=10000, hour=0, lead_day=1
):
    """
    Determine the CWPI sampling distribution.
    """
    
    np.seterr(invalid='ignore')

    obs_resample_u, obs_resample_v = resample_wind_data(
        obs, start_date, end_date, station_list, N=N, hour=hour
    )

    data1_resample_u, data1_resample_v = resample_wind_data(
        data1, start_date, end_date, station_list, N=N, hour=hour, 
        lead_day=lead_day
    )
    data2_resample_u, data2_resample_v = resample_wind_data(
        data2, start_date, end_date, station_list, N=N, hour=hour, 
        lead_day=lead_day
    )

    data1_obs_comp_boot = np.sqrt(
        (data1_resample_u-obs_resample_u) ** 2 + \
        (data1_resample_v-obs_resample_v) ** 2
    )

    data2_obs_comp_boot = np.sqrt(
        (data2_resample_u-obs_resample_u) ** 2 + \
        (data2_resample_v-obs_resample_v) ** 2
    )

    data2_data1_comp_boot = data2_obs_comp_boot - data1_obs_comp_boot
    
    np.seterr(invalid='warn')
    
    return data2_data1_comp_boot

# (Z, group_names, group_lab, fn_prefix = 'group'):

def format_grouped_climatological_data(obs, off, dat, dat_alt, group_names, start_date, end_date, N=1000):
    
    np.seterr(invalid='ignore')
    
    hInd = np.arange(0.0,24.0)
    sInd = np.arange(0, len(group_names))

    cwpi_g = np.zeros((len(group_names), np.size(hInd)))
    cwpi_alt_g = np.zeros((len(group_names), np.size(hInd)))
    cwpi_dat_alt_dat_g = np.zeros((len(group_names), np.size(hInd)))

    cwpi_mean_g = np.zeros((len(group_names), np.size(hInd)))
    cwpi_alt_mean_g = np.zeros((len(group_names), np.size(hInd)))
    cwpi_dat_alt_dat_mean_g = np.zeros((len(group_names), np.size(hInd)))

    cwpi_std_g = np.zeros((len(group_names), np.size(hInd)))
    cwpi_alt_std_g = np.zeros((len(group_names), np.size(hInd)))
    cwpi_dat_alt_dat_std_g = np.zeros((len(group_names), np.size(hInd)))
    
    obs_std_u_g = np.zeros((len(group_names), np.size(hInd)))
    dat_std_u_g = np.zeros((len(group_names), np.size(hInd)))
    dat_alt_std_u_g = np.zeros((len(group_names), np.size(hInd)))
    off_std_u_g = np.zeros((len(group_names), np.size(hInd)))
    
    obs_std_v_g = np.zeros((len(group_names), np.size(hInd)))
    dat_std_v_g = np.zeros((len(group_names), np.size(hInd)))
    dat_alt_std_v_g = np.zeros((len(group_names), np.size(hInd)))
    off_std_v_g = np.zeros((len(group_names), np.size(hInd)))

    for s in np.arange(0,len(group_names)):
        
        for i in np.arange(0,hInd.size):
            
            obs_resample_u, obs_resample_v = resample_wind_data(
                obs, start_date, end_date, list(eval(group_names[s])), N=N, hour=hInd[i]
            )
            off_resample_u, off_resample_v = resample_wind_data(
                off, start_date, end_date, list(eval(group_names[s])), N=N, 
                hour=hInd[i], lead_day=1
            )
            dat_resample_u, dat_resample_v = resample_wind_data(
                dat, start_date, end_date, list(eval(group_names[s])), N=N,
                hour=hInd[i], lead_day=1
            )
            dat_alt_resample_u, dat_alt_resample_v = resample_wind_data(
                dat_alt, start_date, end_date, list(eval(group_names[s])), N=N,
                hour=hInd[i], lead_day=1
            )
            
            cwpi_off_boot = np.sqrt(
                (off_resample_u-obs_resample_u) ** 2 + \
                (off_resample_v-obs_resample_v) ** 2
            )
            cwpi_dat_boot = np.sqrt(
                (dat_resample_u-obs_resample_u) ** 2 + \
                (dat_resample_v-obs_resample_v) ** 2
            )
            cwpi_dat_alt_boot = np.sqrt(
                (dat_alt_resample_u-obs_resample_u) ** 2 + \
                (dat_alt_resample_v-obs_resample_v) ** 2
            )

            cwpi_boot = cwpi_dat_boot - cwpi_off_boot
            cwpi_alt_boot = cwpi_dat_alt_boot - cwpi_off_boot
            cwpi_dat_alt_dat_boot = cwpi_dat_boot - cwpi_dat_alt_boot

            if np.all(np.isnan(cwpi_boot)):
                cwpi_g[s,i] = np.nan
                cwpi_alt_g[s,i] = np.nan
                cwpi_dat_alt_dat_g[s,i] = np.nan

                cwpi_mean_g[s,i] = np.nan
                cwpi_alt_mean_g[s,i] = np.nan
                cwpi_dat_alt_dat_mean_g[s,i] = np.nan

                cwpi_std_g[s,i] = np.nan
                cwpi_alt_std_g[s,i] = np.nan
                cwpi_dat_alt_dat_std_g[s,i] = np.nan
            else:
                cwpi_g[s,i] = (
                    np.sum(cwpi_boot>0)/np.size(cwpi_boot)
                )
                cwpi_alt_g[s,i] = (
                    np.sum(cwpi_alt_boot>0)/np.size(cwpi_alt_boot)
                )
                cwpi_dat_alt_dat_g[s,i] = (
                    np.sum(cwpi_dat_alt_dat_boot>0)/np.size(cwpi_dat_alt_dat_boot)
                )

                cwpi_mean_g[s,i] = np.mean(cwpi_boot)
                cwpi_alt_mean_g[s,i] = np.mean(cwpi_alt_boot)
                cwpi_dat_alt_dat_mean_g[s,i] = np.mean(cwpi_dat_alt_dat_boot)

                cwpi_std_g[s,i] = np.std(cwpi_boot)
                cwpi_alt_std_g[s,i] = np.std(cwpi_alt_boot)
                cwpi_dat_alt_dat_std_g[s,i] = np.std(cwpi_dat_alt_dat_boot)
                
                obs_std_u_g[s,i] = np.nanstd(obs_resample_u)
                obs_std_v_g[s,i] = np.nanstd(obs_resample_v)
                dat_std_u_g[s,i] = np.nanstd(dat_resample_u)
                dat_std_v_g[s,i] = np.nanstd(dat_resample_v)
                dat_alt_std_u_g[s,i] = np.nanstd(dat_alt_resample_u)
                dat_alt_std_v_g[s,i] = np.nanstd(dat_alt_resample_v)
                off_std_u_g[s,i] = np.nanstd(off_resample_u)
                off_std_v_g[s,i] = np.nanstd(off_resample_v)
    
    cwpi_g = np.round(cwpi_g * 100).astype(int)
    cwpi_alt_g = np.round(cwpi_alt_g * 100).astype(int)
    cwpi_dat_alt_dat_g = np.round(cwpi_dat_alt_dat_g * 100).astype(int)
    
    np.seterr(invalid='warn')
    
    return [
        cwpi_g, cwpi_alt_g, cwpi_dat_alt_dat_g, cwpi_mean_g, cwpi_alt_mean_g, cwpi_dat_alt_dat_mean_g,
        cwpi_std_g, cwpi_alt_std_g, cwpi_dat_alt_dat_std_g, obs_std_u_g, obs_std_v_g,
        dat_std_u_g, dat_std_v_g, dat_alt_std_u_g, dat_alt_std_v_g, off_std_u_g, off_std_v_g
    ]

def plot_climatological_group_data_scorecards(Z, group_names, group_lab, fn_prefix = 'group'):

    hInd = np.arange(0.0,24.0)
    sInd = np.arange(0, len(group_names))

    # Create labels for heatmap.
    X, Y = np.meshgrid(hInd, sInd)

    z = [source.flatten() for source in Z]

    z_lab = [z[0].astype(str), z[1].astype(str), z[2].astype(str)]

    # Convert label values to strings
    for i in np.arange(3, len(z)):
        z_lab_i = np.empty(np.size(z[i]))
        for j in np.arange(0,np.size(z[0])):
            z_lab_i[j] = "{:.1f}".format(z[i][j])
        z_lab = z_lab + [z_lab_i.astype('U21')]
        
    z_dat_dat_alt_u_std_min = np.min(np.concatenate((z[11], z[13])))
    z_dat_dat_alt_u_std_max = np.max(np.concatenate((z[11], z[13])))
    z_dat_dat_alt_v_std_min = np.min(np.concatenate((z[12], z[14])))
    z_dat_dat_alt_v_std_max = np.max(np.concatenate((z[12], z[14])))

    z_min = [0, 0, 0, -np.max(np.abs(z[3])), -np.max(np.abs(z[4])), -np.max(np.abs(z[5])), np.min(np.abs(z[6])), 
             np.min(np.abs(z[7])), np.min(np.abs(z[8])), np.min(z[9]), np.min(z[10]), z_dat_dat_alt_u_std_min,
             z_dat_dat_alt_v_std_min, z_dat_dat_alt_u_std_min, z_dat_dat_alt_v_std_min, np.min(z[15]), 
             np.min(z[16])
            ]
    z_max = [100, 100, 100, np.max(np.abs(z[3])), np.max(np.abs(z[4])), np.max(np.abs(z[5])), 
             np.max(np.abs(z[6])), np.max(np.abs(z[7])), np.max(np.abs(z[8])), 
             np.max(z[9]), np.max(z[10]), z_dat_dat_alt_u_std_max,
             z_dat_dat_alt_v_std_max, z_dat_dat_alt_u_std_max, z_dat_dat_alt_v_std_max, np.max(z[15]), 
             np.max(z[16])]

    bar_lab = [
        '[%]', '[%]', '[%]', '[kn]', '[kn]', '[kn]', '[kn]', '[kn]', '[kn]'
    ]
    bar_lab = bar_lab + ['[kn]'] * 8

    title = [
        'Percentage Chance that Official is Better than ' + dat_name, 
        'Percentage Chance that Official is Better than ' + dat_alt_name,
        'Percentage Chance that ' + dat_alt_name + ' is Better than ' + dat_name,
        'Mean Official vs ' + dat_name + ' CWPI', 
        'Mean Official vs ' + dat_alt_name + ' CWPI', 
        'Mean ' + dat_alt_name + ' vs ' + dat_name + ' CWPI', 
        'Standard Deviation Official vs ' + dat_name + ' CWPI', 
        'Standard Deviation Official vs ' + dat_alt_name + ' CWPI', 
        'Standard Deviation ' + dat_alt_name + ' vs ' + dat_name + ' CWPI', 
        'Standard Deviation of Observed Zonal Perturbations',
        'Standard Deviation of Observed Meridional Perturbations',
        'Standard Deviation of ' + dat_name + ' Zonal Perturbations',
        'Standard Deviation of ' + dat_name + ' Meridional Perturbations',
        'Standard Deviation of ' + dat_alt_name + ' Zonal Perturbations',
        'Standard Deviation of ' + dat_alt_name + ' Meridional Perturbations',
        'Standard Deviation of Official Zonal Perturbations',
        'Standard Deviation of Official Meridional Perturbations',
    ]

    file_name = [
        fn_prefix + '_cwpi_', fn_prefix + '_cwpi_alt_', fn_prefix + '_cwpi_dat_alt_dat', 
        fn_prefix + '_cwpi_mean_', fn_prefix + '_cwpi_alt_mean_', fn_prefix + '_cwpi_dat_alt_dat_mean_',
        fn_prefix + '_cwpi_std_', fn_prefix + '_cwpi_alt_std_', fn_prefix + '_cwpi_dat_alt_dat_std_',
    ]
    for source in ['Observed', dat_name, dat_alt_name, 'Official']:
        file_name = file_name + [fn_prefix + 'comp_u_pert_std_' + source, 
                                 fn_prefix + 'comp_v_pert_std_' + source]

    color_scale = [
        'RdBu', 'RdBu', 'RdBu', 'RdBu', 'RdBu', 'RdBu', 'Reds', 'Reds', 'Reds'
    ]
    color_scale = color_scale + ['Reds'] * 8

    x = X.flatten()
    y = Y.flatten()
    
    for i in np.arange(0,len(Z)):

        # Create heat map trace.
        trace_heat = {
            'z' : Z[i],
            'zmin' : z_min[i], 
            'zmax' : z_max[i], 
            'x' : hInd,
            'y' : sInd,
            'type' : 'heatmap',
            'colorbar' : {
                'title' : bar_lab[i],
                'titleside' : 'right',
                'thickness' : 15,
            },
            'colorscale' : color_scale[i],
            'hoverinfo' : 'none',
        }

        # Use a scatterplot trace for the labels. 
        trace_label = {
            'x' : x,
            'y' : y,
            'text' : z_lab[i],
            'textfont' : {
                'size'  : 8,
            },
            'type' : 'scatter',
            'mode' : 'text',
            'name' : bar_lab[i],
        }

        layout = go.Layout(
            title = title[i],
            width = 540,
            height = 230,
            xaxis = dict(
                title = 'Hour [UTC]', showgrid = False, range = [-0.5,23.5],
                autotick = False, dtick = 4,
            ),
            yaxis = go.YAxis(
                tickmode = 'array',
                ticktext = group_lab,
                tickvals=sInd, range = [-0.5, len(group_names) - 0.5],
                title = 'Station', showgrid = False, 
            ),
            hovermode = 'closest',
            margin = {
                't' : 40, 'l' : 140
            },
            font = {
                'family' : 'Times New Roman', 'size' : '10', 'color' : 'black',
            },
        )

        fig = {
            'data': [trace_heat, trace_label], 
            'layout': layout
        }

        iplot(fig)

        file_name_i = file_name[i] + start_date + '_' + end_date + '_' + dat_name

        if save_plot:
            plotly.offline.plot(
                fig,  filename=file_name_i + '.html', image='svg', output_type='file', 
                image_width=600, image_height=240, 
                image_filename=file_name_i + '.svg'
            )
        
    return

## Hodographs

Generate hodograph (a plot showing the evolution of winds with time) for the mean wind perturbations over the climatological period. As above, the hodograph for the 1st July 2017 at Darwin Aiport is considered.

In [131]:
# Specify start and end dates for climatology as yyyy/mm/dd strings.
if season == 'austral_summer':
    start_date = '20171201'
    end_date = '20180228'
elif season == 'austral_winter':
    start_date = '20180601'
    end_date = '20180831'
    
# Specify stations as a numpy array of station ID numbers. 
station_list = np.array(list(darwin_ap))
    
# Calculate hourly mean data. 
obs_h=gen_composite(obs, station_list, start_date, end_date)
off_h=gen_composite(off, station_list, start_date, end_date)
dat_h=gen_composite(dat, station_list, start_date, end_date)
dat_alt_h=gen_composite(dat_alt, station_list, start_date, end_date)

# Specify lead day to plot.
lead_day=1

obs_x, obs_y, obs_lab = format_composite(obs_h)
off_x, off_y, off_lab = format_composite(off_h, lead_day)
dat_x, dat_y, dat_lab = format_composite(dat_h, lead_day)
dat_alt_x, dat_alt_y, dat_alt_lab = format_composite(dat_alt_h, lead_day)

# Plot using plotly.
trace_obs = gen_trace(obs_x, obs_y, obs_lab, 'Observations', 'green', 0)
trace_off = gen_trace(off_x, off_y, off_lab, 'Official', 'red', 0)
trace_dat = gen_trace(dat_x, dat_y, dat_lab, dat_name, 'blue', 0)
trace_dat_alt = gen_trace(dat_alt_x, dat_alt_y, dat_alt_lab, dat_alt_name, 'orange', 0)

layout = {
    'title' : 'Climatological Wind Perturbations: Lead Day %i' % lead_day,
    'width' : 400,
    'height' : 420,
    'xaxis' : {'title': 'u [kn]',},
    'yaxis' : {'title': 'v [kn]', 'scaleanchor' : "x"},
    'hovermode' : 'closest',
    'font' : {
        'family' : 'Times New Roman', 'size' : '12', 'color' : 'black'
    },
    'legend' : {'orientation' : 'h', 'x' : -2.5, 'y' : -.3 }
}

fig = {'data': [trace_obs, trace_off, trace_dat, trace_dat_alt], 
       'layout': layout}

iplot(fig)

if save_plot:
    plotly.offline.plot(
        fig,  filename='clim_winds.html', image='svg', output_type='file', 
        image_width=400, image_height=420, 
        image_filename='clim_winds_' + season + '_' + dat_name
    )

## Verification Across Lead Days

Calculate the $\text{CWPI}$ index and its sampling distribution using bootstrapping. Use the sampling distribution to work out the probability that $\text{CWPI} > 0$ for each hour and lead day. An example $\text{CWPI}$ sampling distribution is considered in the [appendix](#cwpi_sampling_distribution).

In [ ]:
# Number of bootstrapped samples to generate for each hour block and lead day. 
N = 1000

# Diurnal cycle verification index.
prob_cwpi_above_zero=np.empty(obs_h['count'].shape)*np.nan

hInd = obs_h.hour.values
lInd = obs_h.lead_day.values

for i in np.arange(0,hInd.size):
    
    obs_resample_u, obs_resample_v = resample_wind_data(
            obs, start_date, end_date, station_list, N=N, hour=hInd[i]
        )
    
    for j in np.arange(0,lInd.size):
        
        off_resample_u, off_resample_v = resample_wind_data(
            off, start_date, end_date, station_list, N=N, 
            hour=hInd[i], lead_day=lInd[j]
        )
        
        dat_resample_u, dat_resample_v = resample_wind_data(
            dat, start_date, end_date, station_list, N=N,
            hour=hInd[i], lead_day=lInd[j]
        )
        
        cwpi_off_boot = np.sqrt(
            (off_resample_u-obs_resample_u) ** 2 + \
            (off_resample_v-obs_resample_v) ** 2
        )

        cwpi_dat_boot = np.sqrt(
            (dat_resample_u-obs_resample_u) ** 2 + \
            (dat_resample_v-obs_resample_v) ** 2
        )

        cwpi_boot = cwpi_dat_boot - cwpi_off_boot
        
        if np.all(np.isnan(cwpi_boot)):
            prob_cwpi_above_zero[i,j] = np.nan
        else:
            prob_cwpi_above_zero[i,j] = (
                np.sum(cwpi_boot>0)/np.size(cwpi_boot)
            )
        
dims=['hour','lead_day']
coords={'hour':hInd, 'lead_day':lInd}     
prob_cwpi_above_zero=xr.DataArray(
    prob_cwpi_above_zero, dims=dims, coords=coords
)

Plot heatmap of results.

In [ ]:
# Create labels for heatmap.
cwpi_confidence = prob_cwpi_above_zero.dropna(dim = 'lead_day', how='any')

hInd = cwpi_confidence.hour.values
lInd = cwpi_confidence.lead_day.values

# Create labels for heatmap.
X, Y = np.meshgrid(hInd, lInd)
Z = np.round(cwpi_confidence.values.T*100).astype(int)

x = X.flatten()
y = Y.flatten()
z = Z.flatten()

z_lab = z.astype(str)

# Create heat map trace.
trace_heat = {
    'z' : Z,
    'zmin' : 0, 
    'zmax' : 100, 
    'x' : hInd,
    'y' : lInd,
    'type' : 'heatmap',
    'colorbar' : {
        'title' : 'Percentage Chance',
        'titleside' : 'right',
        'tickvals' : [0, 20, 40, 60, 80, 100],
        'thickness' : 15,
    },
    'hoverinfo' : 'none',
}

# Use a scatterplot trace for the labels. 
trace_label = {
    'x' : x,
    'y' : y,
    'text' : z_lab,
    'type' : 'scatter',
    'mode' : 'text',
    'name' : 'Chance',
}

layout = {
    'title' : 'Percentage Chance that Official is Better than ' + dat_name,
    'width' : 800,
    'height' : 350,
    'xaxis' : {
        'title' : 'Hour [UTC]', 'showgrid' : False, 'range' : [-0.5,23.5],
        'autotick' : False, 'dtick' : 4,
    },
    'yaxis' : {
        'title' : 'Lead Day', 'showgrid' : False, 
        'autotick' : False, 'dtick' : 1,
    },
    'hovermode': 'closest',
    'margin' : {
        't' : 80
    },
    'font' : {
        'family' : 'Times New Roman', 'size' : '12', 'color' : 'black',
    }
}

fig = {
    'data': [trace_heat, trace_label], 
    'layout': layout
}

iplot(fig)

if save_plot:
    plotly.offline.plot(
        fig,  filename='cwpi.html', image='svg', output_type='file', 
        image_width=600, image_height=280, 
        image_filename='cwpi_' + season + '_' + dat_name
    )

The above scorecard for the $\text{CWPI}$ indicates that in a climatological sense the official forecast not only outperforms OCF at 01:00, 02:00 and 07:00 UTC, but also between 12:00 and 16:00 UTC (21:30 and 01:30 local time) with 90% confidence, except at 12:00 UTC for lead days 1 and 2, and at 16:00 UTC for lead day 6. These results reflect the hodograph above, with the OCF hodograph overly symmetric and failing to capture the stronger south westerly perturbations in the obervational data between 12:00 and 16:00 UTC. Note that this time range represents the period where the sea-breeze transitions to a land-breeze. The more asymmetric signals in the observational and official forecast data may reflect the complicating effects of the Tiwi Island land-breeze, which can converge with those of the Australian mainland (e.g [https://doi.org10.1007/s00703-011-0180-6](https://doi.org/10.1007/s00703-011-0180-6).) 

The reason this feature shows up in the climatological results but not the daily comparison results is likely due to the different levels of variability in the observational, OCF and official forecast data: for instance the standard deviations of the zonal and meridional wind perturbations $(s_u, s_v)$ at 14:00 UTC for the observation, official and OCF datasets are $(1.90 \text{ kn}, 2.08 \text{ kn})$, $(2.30\text{ kn}, 2.53\text{ kn})$ and $(0.75\text{ kn}, 0.99\text{ kn})$ respectively. Thus on any given day the OCF perturbations may be closer to those observed simply by virtue of being smaller in magnitude and having less variability. 

## Airport Comparison

In [104]:
climatological_data_a = format_grouped_climatological_data(
    obs, off, dat, dat_alt, airport_names, start_date, end_date, N=1000
)

In [105]:
plot_climatological_group_data_scorecards(
    climatological_data_a, airport_names, airport_station_list_lab, fn_prefix = 'airport'
)

## Airport Group Comparison

In [107]:
grouped_climatological_data_a = format_grouped_climatological_data(
    obs, off, dat, dat_alt, airport_station_group_names, start_date, end_date, N=1000
)

In [108]:
plot_climatological_group_data_scorecards(
    grouped_climatological_data_a, airport_station_group_names, airport_station_list_lab, fn_prefix = 'airport'
)

## State Comparison

In [129]:
grouped_climatological_data_c = format_grouped_climatological_data(
    obs, off, dat, dat_alt, coastal_station_group_names, start_date, end_date, N=1000
)

In [130]:
plot_climatological_group_data_scorecards(
    grouped_climatological_data_c, coastal_station_group_names, coastal_station_group_labels,
    fn_prefix = 'coastal'
)

# Additional Metrics #

## Functions

In [112]:
def signed_angular_difference(
    angle1, angle2
):
    """
    Calculate angle1 - angle2, taking smaller angle in absolute value, but 
    preserving sign in result.
    """
    
    diff = angle1 - angle2
    diff = np.mod(diff + 180, 360) - 180
    
    return diff

# def calculate_elliptical_fit(obs, off, dat, dat_alt, group_names, start_date, end_date):
#     lead_day = 1

#     # Create matrix with rows for each station, 
#     # columns u coef cos, u coef sin, v coef cos, v coef sin, hour max, max time, corr coef
#     obs_timing = np.empty((len(group_names),13)) * np.nan
#     off_timing = np.empty((len(group_names),13)) * np.nan
#     dat_timing = np.empty((len(group_names),13)) * np.nan
#     dat_alt_timing = np.empty((len(group_names),13)) * np.nan

#     for s in np.arange(0,len(group_names)):

#         # Calculate hourly mean data. 
#         obs_h=gen_composite(obs, list(eval(group_names[s])), start_date, end_date)
#         off_h=gen_composite(off, list(eval(group_names[s])), start_date, end_date)
#         dat_h=gen_composite(dat, list(eval(group_names[s])), start_date, end_date)
#         dat_alt_h=gen_composite(dat_alt, list(eval(group_names[s])), start_date, end_date)

#         for data in ['obs', 'off', 'dat', 'dat_alt']:

#             a_coef = np.cos(2 * np.pi / 24 * np.arange(0,24))
#             b_coef = np.sin(2 * np.pi / 24 * np.arange(0,24))

#             u = np.squeeze(
#                 eval(data + '_h')['u_pert'].where(eval(data + '_h')['lead_day'] == lead_day). \
#                 dropna('lead_day', how='all').values
#             )

#             v = np.squeeze(
#                 eval(data + '_h')['v_pert'].where(eval(data + '_h')['lead_day'] == lead_day). \
#                 dropna('lead_day', how='all').values
#             )

#             speed = np.sqrt(u ** 2 + v ** 2)
#             hour_max = [i for i, j in enumerate(speed) if j == max(speed)]
#             hour_max = hour_max[0]

#             A = np.array([np.ones(24).T, a_coef.T, b_coef.T]).T

#             a_b = np.linalg.lstsq(A, u, rcond=None)
#             u0 = a_b[0][0]
#             a = a_b[0][1]
#             b = a_b[0][2]
#             c_d = np.linalg.lstsq(A, v, rcond=None)
#             v0 = c_d[0][0]
#             c = c_d[0][1]
#             d = c_d[0][2]

#             # Calculate time when wind aligned with semi major-axis
#             alpha_max = 0.5 * np.arctan(2 * (a * b + c * d) \
#                 / (a ** 2 + c ** 2 - b ** 2 - d ** 2))
#             alpha_max = np.mod(alpha_max * 24 / (2 * np.pi), 12)

#             second_d_test = - a * b * np.sin(2 * np.pi * alpha_max / 12) \
#                 - c * d * np.sin(2 * np.pi * alpha_max / 12)

#             if second_d_test > 0:
#                 alpha_max = np.mod(alpha_max + 6, 12)
#             elif second_d_test == 0:
#                 alpha_max = np.nan

#             u_ellipse = u0 + a * a_coef + b * b_coef
#             v_ellipse = v0 + c * a_coef + d * b_coef

#             # Calculate coefficient of determination using Euclidean norm?
#             SS_tot_u = np.sum((np.mean(u) - u) ** 2)
#             SS_reg_u = np.sum((u - u_ellipse) ** 2)

#             SS_tot_v = np.sum((np.mean(v) - v) ** 2)
#             SS_reg_v = np.sum((v - v_ellipse) ** 2)

#             R_squared_u = 1 - SS_reg_u/SS_tot_u
#             R_squared_v = 1 - SS_reg_v/SS_tot_v

#             semi_major = np.sqrt((a * np.cos(2 * np.pi * alpha_max / 24) \
#                                   + b * np.sin(2 * np.pi * alpha_max / 24)) ** 2 \
#                                 + (c * np.cos(2 * np.pi * alpha_max / 24) \
#                                    + d * np.sin(2 * np.pi * alpha_max / 24)) ** 2)

#             semi_minor = np.sqrt((b * np.cos(2 * np.pi * alpha_max / 24) \
#                                   - a * np.sin(2 * np.pi * alpha_max / 24)) ** 2 \
#                                 + (d * np.cos(2 * np.pi * alpha_max / 24) \
#                                    - c * np.sin(2 * np.pi * alpha_max / 24)) ** 2)

#             phi = np.arctan((c * np.cos(2 * np.pi * alpha_max / 24) \
#                              + d * np.sin(2 * np.pi * alpha_max / 24)) \
#                             /(a * np.cos(2 * np.pi * alpha_max / 24) \
#                               + b * np.sin(2 * np.pi * alpha_max / 24)))

#             phi = np.mod(phi, np.pi)

#             eccentricity = np.sqrt(semi_major ** 2 - semi_minor ** 2) / semi_major

#             eval(data + '_timing')[s,:] = [
#                 u0, a, b, v0, c, d, speed[hour_max], hour_max, 
#                 R_squared_u, R_squared_v, alpha_max, phi, eccentricity
#             ]

#     # Store as xarray datasets
#     ds_list = []
    
#     dims=['station_group']
#     coords={
#         'station_group' : group_names, 
#     }
    
#     for data in ['obs_timing', 'off_timing', 'dat_timing', 'dat_alt_timing']:
#         ds=xr.Dataset(
#             {
#                 'u0' : (dims, eval(data)[:,0]), 'a' : (dims, eval(data)[:,1]), 'b' : (dims, eval(data)[:,2]), 
#                 'v0' : (dims, eval(data)[:,3]), 'c' : (dims, eval(data)[:,4]), 'd' : (dims, eval(data)[:,5]), 
#                 'semi_major' : (dims, eval(data)[:,6]), 'semi_major_hour' : (dims, eval(data)[:,7]), 
#                 'R_squared_u' : (dims, eval(data)[:,8]), 'R_squared_v' : (dims, eval(data)[:,9]), 
#                 'alpha_max' : (dims, eval(data)[:,10]), 'phi' : (dims, eval(data)[:,11]), 
#                 'eccentricity' : (dims, eval(data)[:,12]) 
#             }, 
#             coords=coords
#         )
#         ds_list = ds_list + [ds]
        
#     return ds_list

def calculate_elliptical_fit_alt(obs, off, dat, dat_alt, group_names, start_date, end_date):
    lead_day = 1

    # Create matrix with rows for each station, 
    # columns u coef cos, u coef sin, v coef cos, v coef sin, hour max, max time, corr coef
    obs_timing = np.empty((len(group_names),13)) * np.nan
    off_timing = np.empty((len(group_names),13)) * np.nan
    dat_timing = np.empty((len(group_names),13)) * np.nan
    dat_alt_timing = np.empty((len(group_names),13)) * np.nan

    for s in np.arange(0,len(group_names)):

        # Calculate hourly mean data. 
        obs_h=gen_composite(obs, list(eval(group_names[s])), start_date, end_date)
        off_h=gen_composite(off, list(eval(group_names[s])), start_date, end_date)
        dat_h=gen_composite(dat, list(eval(group_names[s])), start_date, end_date)
        dat_alt_h=gen_composite(dat_alt, list(eval(group_names[s])), start_date, end_date)

        for data in ['obs', 'off', 'dat', 'dat_alt']:
                        
            u = np.squeeze(
                eval(data + '_h')['u_pert'].where(eval(data + '_h')['lead_day'] == lead_day). \
                dropna('lead_day', how='all').values
            )

            v = np.squeeze(
                eval(data + '_h')['v_pert'].where(eval(data + '_h')['lead_day'] == lead_day). \
                dropna('lead_day', how='all').values
            )

            pert = np.stack((u,v))
            
            def res(x, t_p, pert):
                return np.sqrt( 
                    (x[0] + x[1] * np.cos(np.pi * (np.sin(np.pi * ((np.mod(t_p - x[6],24) / 24) - 0.5)) + 1)) \
                     + x[2] * np.sin(np.pi * (np.sin(np.pi * ((np.mod(t_p - x[6],24) / 24) - 0.5)) + 1)) \
                     - pert[0]) ** 2 \
                    + (x[3] + x[4] * np.cos(np.pi * (np.sin(np.pi * ((np.mod(t_p - x[6],24) / 24) - 0.5)) + 1)) \
                       + x[5] * np.sin(np.pi * (np.sin(np.pi * ((np.mod(t_p - x[6],24) / 24) - 0.5)) + 1)) 
                       - pert[1]) ** 2
                )
             
            x_min = [-5, -10, -10, -5, -10, -10, 0]
            x_max = [5, 10, 10, 5, 10, 10, 24]
            x0 = [0, 0, 0, 0, 0, 0, 18]
            
            t = np.arange(0,24)
            
            res_lsq = least_squares(
                res, x0, args=(t, pert), bounds=(x_min, x_max), loss='soft_l1'
            )
            [u0, a, b, v0, c, d, psi] = res_lsq.x
            
            # Calculate time when wind aligned with semi major-axis
            alpha_max = 0.5 * np.arctan(2 * (a * b + c * d) \
                / (a ** 2 + c ** 2 - b ** 2 - d ** 2))

            second_d_test = - a * b * np.sin(alpha_max) \
                - c * d * np.sin(alpha_max)

#             pdb.set_trace()
    
            if second_d_test > 0:
                alpha_max_a = np.mod(alpha_max + np.pi/2, 2 * np.pi)
                alpha_max_b = np.mod(alpha_max + 3 * np.pi/2, 2 * np.pi)
            elif second_d_test < 0:
                alpha_max_a = np.mod(alpha_max, 2 * np.pi)
                alpha_max_b = np.mod(alpha_max + np.pi, 2 * np.pi)
            elif second_d_test == 0:
                alpha_max_a = np.nan
                alpha_max_b = np.nan
                
            time_aligned_semi_major_a = np.mod(
                (24 / np.pi) * (np.arcsin(alpha_max_a / np.pi - 1) + np.pi/2) + psi, 24
            )
            time_aligned_semi_major_b = np.mod(
                (24 / np.pi) * (np.arcsin(alpha_max_b / np.pi - 1) + np.pi/2) + psi, 24
            )

            if (time_aligned_semi_major_a > 3 and time_aligned_semi_major_a <= 15):
                time_aligned_semi_major = time_aligned_semi_major_a
            else:
                time_aligned_semi_major = time_aligned_semi_major_b
                
            if second_d_test > 0:
                alpha_max = np.mod(alpha_max + np.pi/2, np.pi)
            elif second_d_test < 0:
                alpha_max = np.mod(alpha_max, np.pi)
            elif second_d_test == 0:
                alpha_max = np.nan
            
#             time_aligned_semi_major = np.mod(time_aligned_semi_major, 12)

            a_coef = np.cos(np.pi * (np.sin(np.pi * ((np.mod(t - psi, 24) / 24) - 0.5)) + 1))
            b_coef = np.sin(np.pi * (np.sin(np.pi * ((np.mod(t - psi, 24) / 24) - 0.5)) + 1))
                
            u_ellipse = u0 + a * a_coef + b * b_coef
            v_ellipse = v0 + c * a_coef + d * b_coef

            # Calculate coefficient of determination using Euclidean norm?
            SS_tot_u = np.sum((np.mean(u) - u) ** 2)
            SS_reg_u = np.sum((u - u_ellipse) ** 2)

            SS_tot_v = np.sum((np.mean(v) - v) ** 2)
            SS_reg_v = np.sum((v - v_ellipse) ** 2)

            R_squared_u = 1 - SS_reg_u/SS_tot_u
            R_squared_v = 1 - SS_reg_v/SS_tot_v

            semi_major = np.sqrt((a * np.cos(alpha_max) \
                                  + b * np.sin(alpha_max)) ** 2 \
                                + (c * np.cos(alpha_max) \
                                   + d * np.sin(alpha_max)) ** 2)

            semi_minor = np.sqrt((b * np.cos(alpha_max) \
                                  - a * np.sin(alpha_max)) ** 2 \
                                + (d * np.cos(alpha_max) \
                                   - c * np.sin(alpha_max)) ** 2)

            phi = np.arctan((c * np.cos(alpha_max) \
                             + d * np.sin(alpha_max)) \
                            /(a * np.cos(alpha_max) \
                              + b * np.sin(alpha_max)))

            phi = np.mod(phi, np.pi)
            phi = 180 * phi / np.pi

            eccentricity = np.sqrt(semi_major ** 2 - semi_minor ** 2) / semi_major
            
            eval(data + '_timing')[s,:] = [
                u0, a, b, v0, c, d, semi_major, time_aligned_semi_major, 
                R_squared_u, R_squared_v, phi, eccentricity, psi
            ]

    # Store as xarray datasets
    ds_list = []
    
    dims=['station_group']
    coords={
        'station_group' : group_names, 
    }
    
    for data in ['obs_timing', 'off_timing', 'dat_timing', 'dat_alt_timing']:
        ds=xr.Dataset(
            {
                'u0' : (dims, eval(data)[:,0]), 'a' : (dims, eval(data)[:,1]), 'b' : (dims, eval(data)[:,2]), 
                'v0' : (dims, eval(data)[:,3]), 'c' : (dims, eval(data)[:,4]), 'd' : (dims, eval(data)[:,5]), 
                'semi_major' : (dims, eval(data)[:,6]), 'time_aligned_semi_major' : (dims, eval(data)[:,7]), 
                'R_squared_u' : (dims, eval(data)[:,8]), 'R_squared_v' : (dims, eval(data)[:,9]), 
                'phi' : (dims, eval(data)[:,10]), 'eccentricity' : (dims, eval(data)[:,11]), 
                'psi' : (dims, eval(data)[:,12])  
                
            }, 
            coords=coords
        )
        ds_list = ds_list + [ds]
        
    return ds_list

def format_ellipse_data(obs_e, off_e, dat_e, dat_alt_e, group_names):
    
    dInd = np.arange(0, 4)
    sInd = np.arange(0, len(group_names))
    
    R_squared_u = np.zeros((np.size(dInd), np.size(sInd)))
    R_squared_v = np.zeros((np.size(dInd), np.size(sInd)))
    semi_major = np.zeros((np.size(dInd), np.size(sInd)))
    phi = np.zeros((np.size(dInd), np.size(sInd)))
    eccentricity = np.zeros((np.size(dInd), np.size(sInd)))
    time_aligned_semi_major = np.zeros((np.size(dInd), np.size(sInd)))

    d_list = ['obs_e', 'off_e', 'dat_e', 'dat_alt_e']
    
    for d in np.arange(0,dInd.size):
        for s in np.arange(0,len(group_names)):            
            R_squared_u[d,s] = eval(d_list[d]).R_squared_u.values[s]*100
            R_squared_v[d,s] = eval(d_list[d]).R_squared_v.values[s]*100
            semi_major[d,s] = eval(d_list[d]).semi_major.values[s]
            phi[d,s] = eval(d_list[d]).phi.values[s]
            eccentricity[d,s] = eval(d_list[d]).eccentricity.values[s]*100
            time_aligned_semi_major[d,s] = eval(d_list[d]).time_aligned_semi_major.values[s]
    
    return [
        R_squared_u, R_squared_v, semi_major, phi, eccentricity, time_aligned_semi_major,
    ]

def plot_ellipse_scorecards(Z, group_names, group_lab, fn_prefix = 'group'):

    dInd = np.arange(0, 4)
    sInd = np.arange(0, len(group_names))

    d_names = ['AWS', 'Official', dat_name, dat_alt_name]

    # Create labels for heatmap.
    X, Y = np.meshgrid(sInd, dInd)

    z = [source.flatten() for source in Z]
    z_lab = []

    decimal_profile = ['{:.0f}', '{:.0f}', '{:.1f}', '{:.0f}', '{:.0f}', '{:.1f}']
    
    # Convert label values to strings
    for i in np.arange(0, len(z)):
        z_lab_i = np.empty(np.size(z[i]))
        for j in np.arange(0,np.size(z[0])):
            z_lab_i[j] = decimal_profile[i].format(z[i][j])
        z_lab_i = np.array(list(str(k)[-2:] == '.0' and str(k)[:-2] or str(k) for k in z_lab_i))
        z_lab = z_lab + [z_lab_i.astype('U21')]
        
    z_min = [0, 0, np.min(z[2]), 0, 0, 0]
    z_max = [100, 100, np.max(z[2]), 180, 100, 24]

    bar_lab = ['[percent]', '[percent]', '[kn]', '[degrees]', '[percent]', '[hours]']

    title = [
        'Zonal Perturbation R^2 Coefficient', 
        'Meridional Perturbation R^2 Coefficient',
        'Amplitude',
        'Angle of Semi-Major Axis', 
        'Eccentricity', 
        'Time Winds Aligned with Semi-Major Axis',
    ]

    file_name = [
        fn_prefix + 'zonal_r2', 
        fn_prefix + 'meridional_r2',
        fn_prefix + 'semi_major', 
        fn_prefix + 'phi',
        fn_prefix + 'eccentricity', 
        fn_prefix + 'time_aligned_semi_major',
    ]

    n=180
    angle_pallete = sns.color_palette("husl", n+1)
    color_ind = np.arange(0,n+1)/n
    cyclic_cmap = []
    for i in np.arange(0,n+1):
        c_str = 'rgb(' + str(int(angle_pallete[i][0]*256)) + ', ' + str(int(angle_pallete[i][1]*256)) \
            + ', ' + str(int(angle_pallete[i][2]*256)) + ')'
        cyclic_cmap = cyclic_cmap + [[color_ind[i], c_str]]
    
    color_scale = [
        'Reds', 'Reds', 'Reds', cyclic_cmap, 'Reds', cyclic_cmap
    ]

    x = X.flatten()
    y = Y.flatten()
    
    for i in np.arange(0,len(Z)):

        # Create heat map trace.
        trace_heat = {
            'z' : Z[i],
            'zmin' : z_min[i], 
            'zmax' : z_max[i], 
            'x' : sInd,
            'y' : dInd,
            'type' : 'heatmap',
            'colorbar' : {
                'title' : bar_lab[i],
                'titleside' : 'right',
                'thickness' : 15,
            },
            'colorscale' : color_scale[i],
            'hoverinfo' : 'none',
        }

        # Use a scatterplot trace for the labels. 
        trace_label = {
            'x' : x,
            'y' : y,
            'text' : z_lab[i],
            'textfont' : {
                'size'  : 8,
            },
            'type' : 'scatter',
            'mode' : 'text',
            'name' : bar_lab[i],
        }

        layout = go.Layout(
            title = title[i],
            width = 380,
            height = 200,
            xaxis = dict(
                tickmode = 'array',
                ticktext = group_lab,
                tickvals=sInd, range = [-0.5, len(group_names) - 0.5],
                title = 'Station', showgrid = False, 
            ),
            yaxis = go.YAxis(
                tickmode = 'array',
                title = 'Dataset', showgrid = False,
                autotick = False, dtick = 1, ticktext = d_names, tickvals=dInd
            ),
            hovermode = 'closest',
            margin = {
                't' : 40, 'l' : 140
            },
            font = {
                'family' : 'Times New Roman', 'size' : '10', 'color' : 'black',
            },
        )

        fig = {
            'data': [trace_heat, trace_label], 
            'layout': layout
        }

        iplot(fig)

        file_name_i = file_name[i] + start_date + '_' + end_date + '_' + dat_name

        if save_plot:
            plotly.offline.plot(
                fig,  filename=file_name_i + '.html', image='svg', output_type='file', 
                image_width=600, image_height=240, 
                image_filename=file_name_i + '.svg'
            )
        
    return

## Ellipse Fit

Can estimate rough shape of diurnal cycle by fitting an ellipse to the climatological hodograph.

In [123]:
[obs_e, off_e, dat_e, dat_alt_e] = calculate_elliptical_fit_alt(
    obs, off, dat, dat_alt, coastal_station_group_names, start_date, end_date
)

In [124]:
f_ellipse_data = format_ellipse_data(obs_e, off_e, dat_e, dat_alt_e, coastal_station_group_names)
plot_ellipse_scorecards(f_ellipse_data, coastal_station_group_names, coastal_station_group_labels, fn_prefix = 'coastal')

In [118]:
# Plot using plotly.
station_group = 'sydney_ap'

obs_e_s = obs_e.where(obs_e['station_group'] == station_group).dropna(dim='station_group', how='all')
off_e_s = off_e.where(off_e['station_group'] == station_group).dropna(dim='station_group', how='all')
dat_e_s = dat_e.where(dat_e['station_group'] == station_group).dropna(dim='station_group', how='all')
dat_alt_e_s = dat_alt_e.where(obs_e['station_group'] == station_group).dropna(dim='station_group', how='all')

uv_list = []
for source in ['obs_e_s', 'off_e_s', 'dat_e_s', 'dat_alt_e_s']:
        
    t = np.arange(0, 24)
    
    a_coef = np.cos(np.pi * (np.sin(np.pi * ((np.mod(t - eval(source).psi.values, 24) / 24) - 0.5)) + 1))
    b_coef = np.sin(np.pi * (np.sin(np.pi * ((np.mod(t - eval(source).psi.values, 24) / 24) - 0.5)) + 1))

    u = eval(source).u0.values + eval(source).a.values * a_coef + eval(source).b.values * b_coef
    v = eval(source).v0.values + eval(source).c.values * a_coef + eval(source).d.values * b_coef
    uv_list = uv_list + [u, v]
    
[obs_u, obs_v, off_u, off_v, dat_u, dat_v, dat_alt_u, dat_alt_v] = uv_list
    
obs_lab = np.empty(24, dtype = '<U21')
off_lab = np.empty(24, dtype = '<U21')
dat_lab = np.empty(24, dtype = '<U21')
dat_alt_lab = np.empty(24, dtype = '<U21')

for i in np.arange(0,24):
    obs_lab[i] = (
        '%05.2f' % np.sqrt(obs_u[i] ** 2 + obs_v[i] ** 2) + \
        ' kn </br>' + str(i) + ' UTC'
    )
    off_lab[i] = (
        '%05.2f' % np.sqrt(off_u[i] ** 2 + off_v[i] ** 2) + \
        ' kn </br>' + str(i) + ' UTC'
    )
    dat_lab[i] = (
        '%05.2f' % np.sqrt(dat_u[i] ** 2 + dat_v[i] ** 2) + \
        ' kn </br>' + str(i) + ' UTC'
    )
    dat_alt_lab[i] = (
        '%05.2f' % np.sqrt(off_u[i] ** 2 + off_v[i] ** 2) + \
        ' kn </br>' + str(i) + ' UTC'
    )

trace1 = gen_trace(obs_u, obs_v, obs_lab, name='Observations', colour='green')
trace2 = gen_trace(off_u, off_v, off_lab, name='Official', colour='red')
trace3 = gen_trace(dat_u, dat_v, dat_lab, name=dat_name, colour='blue')
trace4 = gen_trace(dat_alt_u, dat_alt_v, dat_alt_lab, name=dat_alt_name, colour='brown')

layout = {
    'title' : 'Elliptical Best Fit',
    'width' : 450,
    'height' : 450,
    'xaxis' : {'title': 'u [kn]',},
    'yaxis' : {'title': 'v [kn]', 'scaleanchor' : "x"},
    'hovermode' : 'closest',
    'font' : {
        'family' : 'Times New Roman', 'size' : '12', 'color' : 'black'
    },
    'legend' : {'orientation' : 'h', 'x' : -2.5, 'y' : -.3 }
}

fig = {'data': [trace1, trace2, trace3, trace4], 
       'layout': layout}

iplot(fig)

if save_plot:
    plotly.offline.plot(
        fig,  filename='ellipse_fit.html', image='svg', output_type='file', 
        image_width=450, image_height=450, 
        image_filename='ellipse_' + season + '_' + dat_name
    )

In [ ]:
tt = np.arange(0,24)
psi_prime = 18
time = np.pi * (np.sin(np.pi * ((np.mod(np.arange(0,24)-psi_prime,24) / 24) - 0.5)) + 1)
# t = 12+12*np.sin(np.pi*(tt-12)/24)

psi = np.pi * psi_prime / 12
# x = 1*np.cos(np.pi*t/24) + -1*np.sin(np.pi*t/24)
# y = 1*np.cos(np.pi*t/24) + 1*np.sin(np.pi*t/24)
x = -1*np.cos(time) + 1*np.sin(time)
y = 1*np.cos(time) + 1*np.sin(time)
plt.plot(x,y,'o')
for i in tt: 
    plt.annotate(tt[i].astype(str),(x[i],y[i]))

# Appendix 

This appendix provides examples of the sampling distributions for the $\text{WPI}$ and $\text{CWPI}$. 

## WPI Sampling Distribution

<a id='wpi_sampling_distribution'></a> Recall that the sampling distribution for $\text{WPI}$ is calculated by the Jive `aggregate` function, which assumes it is approximately $t$-distributed; this assumption is valid when $\text{WPI}$ is normally distributed. Consider first the distribution of $\text{WPI}$ for a specific hour and lead day; by default hour 0 and lead day 1 are used.

In [ ]:
hour = 1
lead_day = 1

# Create a meshgrid of the stations to average over
X, Y = np.meshgrid(wpi['wpi']['station_number'].values, darwin_ap_stations)
focus_stations=np.any(X==Y,0)

wpi_example = np.squeeze(
    wpi['wpi'].where(wpi['wpi']['lead_day'] == lead_day). \
    where(wpi['wpi']['valid_start.hour'] == hour). \
    where(wpi['wpi']['station_number'][focus_stations]).\
    mean(dim = 'station_number', skipna=True). \
    dropna('valid_start', how='all'). \
    dropna('lead_day', how='all').values
)

sample_mean=np.nanmean(wpi_example)
sample_std=np.nanstd(wpi_example)
sample_N=wpi_example.size

bin_start=np.round(sample_mean)-5*np.ceil(sample_std)
bin_end=np.round(sample_mean)+5*np.ceil(sample_std)
bin_size=np.ceil(sample_std)/5

trace_hist = {
    'x' : wpi_example,
    'xbins' : {'start':bin_start, 'end':bin_end, 'size':bin_size},
    'name' : 'Data',
    'type' : 'histogram',
    'histnorm' : 'probability density'
}

layout = {
    'title' : 'Distribution of WPI ',
    'width' : 700,
    'height' : 500,
    'xaxis' : {'title' : 'WPI',},
    'yaxis' : {'title' : 'Probability Density', 'tick0' : 0},
    'hovermode': 'closest',  
    'font' : {
        'family' : 'Times New Roman', 'size' : '12'
    }
}

fig = {
    'data': [trace_hist], 
    'layout': layout
}

iplot(fig)

Note that the distribution of $\text{WPI}$ does not appear normal in this example; it is skewed left. To investigate how this effects the sampling distribution of the mean of $\text{WPI}$ the sampling distribution is calculated by bootstrapping and compared with the corresponding $t$-distribution. 

In [ ]:
N=10000

wpi_mean_sampling_dist = np.empty(N)*np.nan

for i in np.arange(0,N):
    wpi_mean_sampling_dist[i] = np.mean(resample(wpi_example)) 
    
dataset = wpi_mean_sampling_dist
sampling_dist_mean=np.mean(wpi_mean_sampling_dist)
sampling_dist_std=np.std(wpi_mean_sampling_dist)
sampling_dist_N=wpi_mean_sampling_dist.size

bin_start=np.round(sampling_dist_mean)-1*np.ceil(sampling_dist_std)
bin_end=np.round(sampling_dist_mean)+2*np.ceil(sampling_dist_std)
bin_size=np.ceil(sampling_dist_std)/20

trace_hist = {
    'x' : wpi_mean_sampling_dist,
    'xbins' : {'start':bin_start, 'end':bin_end, 'size':bin_size},
    'name' : 'Bootstrap',
    'type' : 'histogram',
    'histnorm' : 'probability density'
}

pdf_x = np.arange(bin_start,bin_end,0.01)
pdf_std = sample_std / np.sqrt(sample_N)
pdf_y = ss.t.pdf(
    pdf_x, sampling_dist_N - 1, loc=sample_mean, scale=pdf_std
)

trace_pdf = {
    'x' : pdf_x,
    'y' : pdf_y,
    'name' : 't-Distribution',
    'type' : 'scatter',
    'mode' : 'lines',
    'line' : {'color' : 'red'}
}

layout = {
    'title' : 'Sampling Distribution of Mean WPI',
    'width' : 500,
    'height' : 400,
    'xaxis' : {'title' : 'Mean of WPI',},
    'yaxis' : {'title' : 'Probability Density', 'tick0' : 0},
    'hovermode': 'closest',    
    'font' : {
        'family' : 'Times New Roman', 'size' : '12'
    }
}

fig = {
    'data': [trace_hist, trace_pdf], 
    'layout': layout
}

iplot(fig)

Thus for this example the $t$-distribution is an excellent approximation to the sampling distribution.   

## CWPI Sampling Distribution

<a id='cwpi_sampling_distribution'></a> The following histogram provides an example of the $\text{CWPI}$ sampling distribution calculated by bootstrapping.  

In [ ]:
# Size of bootstrap sample
N = 1000
hour = 0
lead_day = 1

dat_off_comp_boot = clim_index_dist(
    obs, off, dat, N=N, hour=hour, lead_day=lead_day
)

dataset = dat_off_comp_boot
sample_mean=np.mean(dataset)
sample_std=np.std(dataset)
N=dataset.size

bin_start=np.round(sample_mean)-5*np.ceil(sample_std)
bin_end=np.round(sample_mean)+5*np.ceil(sample_std)
bin_size=np.ceil(sample_std)/10

trace_hist = {
    'x' : dataset,
    'xbins' : {'start':bin_start, 'end':bin_end, 'size':bin_size},
    'name' : 'Data',
    'type' : 'histogram',
    'histnorm' : 'probability density'
}

layout = {
    'title' : 'Sampling Distribution of CWPI ',
    'width' : 500,
    'height' : 400,
    'xaxis' : {'title' : 'CWPI',},
    'yaxis' : {'title' : 'Probability Density', 'tick0' : 0},
    'hovermode': 'closest',
    'font' : {
        'family' : 'Times New Roman', 'size' : '12'
    }
}

fig = {
    'data': [trace_hist], 
    'layout': layout
}

iplot(fig)